# Based
- https://www.kaggle.com/code/honganzhu/cmi-piu-competition?scriptVersionId=201912528 Version44 LB0.492

 If you find this notebook useful, please upvote this and the based one.

In [90]:
import numpy as np
import pandas as pd
import os
import re
from sklearn.base import clone
from sklearn.metrics import cohen_kappa_score
from sklearn.model_selection import StratifiedKFold
from scipy.optimize import minimize
from concurrent.futures import ThreadPoolExecutor
from tqdm import tqdm
import polars as pl
import polars.selectors as cs
import matplotlib.pyplot as plt
from matplotlib.ticker import MaxNLocator, FormatStrFormatter, PercentFormatter
import seaborn as sns

from sklearn.preprocessing import StandardScaler
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import torch.optim as optim

from colorama import Fore, Style
from IPython.display import clear_output
import warnings
import lightgbm as lgb
from lightgbm import LGBMRegressor
from xgboost import XGBRegressor
from catboost import CatBoostRegressor
from sklearn.ensemble import VotingRegressor, RandomForestRegressor, GradientBoostingRegressor
from sklearn.impute import SimpleImputer, KNNImputer
from sklearn.pipeline import Pipeline
from pytorch_tabnet.tab_model import TabNetRegressor
warnings.filterwarnings('ignore')
pd.options.display.max_columns = None
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_colwidth', None)

pl.Config.set_tbl_rows(-1)
pl.Config.set_tbl_cols(-1)
pl.Config.set_fmt_str_lengths(10000)

polars.config.Config

In [2]:
#from IPython.display import display as ipydisplay, HTML
#ipydisplay(HTML("<style>.jp-CodeCell.jp-mod-outputsScrolled .jp-Cell-outputArea { max-height: 80em; }</style>"))

In [3]:
SEED = 42
n_splits = 5

# Feature Engineering

- **Feature Selection**: The dataset contains features related to physical characteristics (e.g., BMI, Height, Weight), behavioral aspects (e.g., internet usage), and fitness data (e.g., endurance time). 
- **Categorical Feature Encoding**: Categorical features are mapped to numerical values using custom mappings for each unique category within the dataset. This ensures compatibility with machine learning algorithms that require numerical input.
- **Time Series Aggregation**: Time series statistics (e.g., mean, standard deviation) from the actigraphy data are computed and merged into the main dataset to create additional features for model training.


In [4]:
path = "I:/Kaggle/child-mind-institute-problematic-internet-use/"

In [5]:
train = pd.read_csv(path + 'train.csv', dtype={'id': str})
test = pd.read_csv(path + 'test.csv', dtype={'id': str})
sample = pd.read_csv(path + 'sample_submission.csv', dtype={'id': str})

In [6]:
print(train.shape)
train.head()

(3960, 82)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00008ff9                      Fall                5                0   
1  000fd460                    Summer                9                0   
2  00105258                    Summer               10                1   
3  00115b9f                    Winter                9                0   
4  0016bb22                    Spring               18                1   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0      Winter             51.0            Fall     16.877316             46.0   
1         NaN              NaN            Fall     14.035590             48.0   
2        Fall             71.0            Fall     16.648696             56.5   
3        Fall             71.0          Summer     18.292347             56.0   
4      Summer              NaN             NaN           NaN              NaN   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             50.8                           NaN                    NaN   
1             46.0                          22.0                   75.0   
2             75.6                           NaN                   65.0   
3             81.6                           NaN                   60.0   
4              NaN                           NaN                    NaN   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                 NaN                   NaN                      NaN   
1                70.0                 122.0                      NaN   
2                94.0                 117.0                     Fall   
3                97.0                 117.0                   Summer   
4                 NaN                   NaN                      NaN   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          5.0                          7.0   
3                          6.0                          9.0   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                         NaN       Fall         0.0              0.0   
1                         NaN       Fall         3.0              0.0   
2                        33.0       Fall        20.0              1.0   
3                        37.0     Summer        18.0              1.0   
4                         NaN        NaN         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         0.0   
1           NaN                NaN          NaN               NaN         5.0   
2          10.2                1.0         14.7               2.0         7.0   
3           NaN                NaN          NaN               NaN         5.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          6.0   
1              0.0         11.0               1.0         11.0   
2              1.0         10.0               1.0         10.0   
3              0.0          7.0               0.0          7.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         6.0              1.0       Fall   
1               1.0         3.0              0.0     Winter   
2               1.0         5.0              0.0        NaN   
3               0.0         7.0              1.0     Summer   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         2.0     

In [7]:
print(test.shape)
test.head()

(20, 59)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00008ff9                      Fall                5                0   
1  000fd460                    Summer                9                0   
2  00105258                    Summer               10                1   
3  00115b9f                    Winter                9                0   
4  0016bb22                    Spring               18                1   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0      Winter             51.0            Fall     16.877316             46.0   
1         NaN              NaN            Fall     14.035590             48.0   
2        Fall             71.0            Fall     16.648696             56.5   
3        Fall             71.0          Summer     18.292347             56.0   
4      Summer              NaN             NaN           NaN              NaN   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             50.8                           NaN                    NaN   
1             46.0                          22.0                   75.0   
2             75.6                           NaN                   65.0   
3             81.6                           NaN                   60.0   
4              NaN                           NaN                    NaN   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                 NaN                   NaN                      NaN   
1                70.0                 122.0                      NaN   
2                94.0                 117.0                     Fall   
3                97.0                 117.0                   Summer   
4                 NaN                   NaN                      NaN   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          5.0                          7.0   
3                          6.0                          9.0   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                         NaN       Fall         0.0              0.0   
1                         NaN       Fall         3.0              0.0   
2                        33.0       Fall        20.0              1.0   
3                        37.0     Summer        18.0              1.0   
4                         NaN        NaN         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         0.0   
1           NaN                NaN          NaN               NaN         5.0   
2          10.2                1.0         14.7               2.0         7.0   
3           NaN                NaN          NaN               NaN         5.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          6.0   
1              0.0         11.0               1.0         11.0   
2              1.0         10.0               1.0         10.0   
3              0.0          7.0               0.0          7.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         6.0              1.0       Fall   
1               1.0         3.0              0.0     Winter   
2               1.0         5.0              0.0        NaN   
3               0.0         7.0              1.0     Summer   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         2.0     

In [8]:
sample

id  sii
0   00008ff9    0
1   000fd460    1
2   00105258    2
3   00115b9f    3
4   0016bb22    0
5   001f3379    1
6   0038ba98    2
7   0068a485    3
8   0069fbed    0
9   0083e397    1
10  0087dd65    2
11  00abe655    3
12  00ae59c9    0
13  00af6387    1
14  00bd4359    2
15  00c0cd71    3
16  00d56d4b    0
17  00d9913d    1
18  00e6167c    2
19  00ebc35d    3

In [9]:
data_dict = pd.read_csv(path + 'data_dictionary.csv')
print(data_dict.shape)
data_dict

(81, 6)


Instrument  \
0                                      Identifier   
1                                    Demographics   
2                                    Demographics   
3                                    Demographics   
4              Children's Global Assessment Scale   
5              Children's Global Assessment Scale   
6                               Physical Measures   
7                               Physical Measures   
8                               Physical Measures   
9                               Physical Measures   
10                              Physical Measures   
11                              Physical Measures   
12                              Physical Measures   
13                              Physical Measures   
14               FitnessGram Vitals and Treadmill   
15               FitnessGram Vitals and Treadmill   
16               FitnessGram Vitals and Treadmill   
17               FitnessGram Vitals and Treadmill   
18                              FitnessGram Child   
19                              FitnessGram Child   
20                              FitnessGram Child   
21                              FitnessGram Child   
22                              FitnessGram Child   
23                              FitnessGram Child   
24                              FitnessGram Child   
25                              FitnessGram Child   
26                              FitnessGram Child   
27                              FitnessGram Child   
28                              FitnessGram Child   
29                              FitnessGram Child   
30                              FitnessGram Child   
31                              FitnessGram Child   
32                              FitnessGram Child   
33                Bio-electric Impedance Analysis   
34                Bio-electric Impedance Analysis   
35                Bio-electric Impedance Analysis   
36                Bio-electric Impedance Analysis   
37                Bio-electric Impedance Analysis   
38                Bio-electric Impedance Analysis   
39                Bio-electric Impedance Analysis   
40                Bio-electric Impedance Analysis   
41                Bio-electric Impedance Analysis   
42                Bio-electric Impedance Analysis   
43                Bio-electric Impedance Analysis   
44                Bio-electric Impedance Analysis   
45                Bio-electric Impedance Analysis   
46                Bio-electric Impedance Analysis   
47                Bio-electric Impedance Analysis   
48                Bio-electric Impedance Analysis   
49                Bio-electric Impedance Analysis   
50  Physical Activity Questionnaire (Adolescents)   
51  Physical Activity Questionnaire (Adolescents)   
52     Physical Activity Questionnaire (Children)   
53     Physical Activity Questionnaire (Children)   
54           Parent-Child Internet Addiction Test   
55           Parent-Child Internet Addiction Test   
56           Parent-Child Internet Addiction Test   
57           Parent-Child Internet Addiction Test   
58           Parent-Child Internet Addiction Test   
59           Parent-Child Internet Addiction Test   
60           Parent-Child Internet Addiction Test   
61           Parent-Child Internet Addiction Test   
62           Parent-Child Internet Addiction Test   
63           Parent-Child Internet Addiction Test   
64           Parent-Child Internet Addiction Test   
65           Parent-Child Internet Addiction Test   
66           Parent-Child Internet Addiction Test   
67           Parent-Child Internet Addiction Test   
68           Parent-Child Internet Addiction Test   
69           Parent-Child Internet Addiction Test   
70           Parent-Child Internet Addiction Test   
71           Parent-Child Internet Addiction Test   
72           Parent-Child Internet Addiction Test   
73           Parent-Child Internet Addiction Test   
74           Parent-Child Internet Addiction Test   
75         

In [10]:
train['id'].nunique()

3960

In [11]:
test['id'].nunique()

20

In [12]:
train_target = train[test.columns]

In [13]:
print(train_target.shape)
train_target.head()

(3960, 59)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00008ff9                      Fall                5                0   
1  000fd460                    Summer                9                0   
2  00105258                    Summer               10                1   
3  00115b9f                    Winter                9                0   
4  0016bb22                    Spring               18                1   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0      Winter             51.0            Fall     16.877316             46.0   
1         NaN              NaN            Fall     14.035590             48.0   
2        Fall             71.0            Fall     16.648696             56.5   
3        Fall             71.0          Summer     18.292347             56.0   
4      Summer              NaN             NaN           NaN              NaN   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             50.8                           NaN                    NaN   
1             46.0                          22.0                   75.0   
2             75.6                           NaN                   65.0   
3             81.6                           NaN                   60.0   
4              NaN                           NaN                    NaN   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                 NaN                   NaN                      NaN   
1                70.0                 122.0                      NaN   
2                94.0                 117.0                     Fall   
3                97.0                 117.0                   Summer   
4                 NaN                   NaN                      NaN   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          5.0                          7.0   
3                          6.0                          9.0   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                         NaN       Fall         0.0              0.0   
1                         NaN       Fall         3.0              0.0   
2                        33.0       Fall        20.0              1.0   
3                        37.0     Summer        18.0              1.0   
4                         NaN        NaN         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         0.0   
1           NaN                NaN          NaN               NaN         5.0   
2          10.2                1.0         14.7               2.0         7.0   
3           NaN                NaN          NaN               NaN         5.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          6.0   
1              0.0         11.0               1.0         11.0   
2              1.0         10.0               1.0         10.0   
3              0.0          7.0               0.0          7.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         6.0              1.0       Fall   
1               1.0         3.0              0.0     Winter   
2               1.0         5.0              0.0        NaN   
3               0.0         7.0              1.0     Summer   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         2.0     

In [14]:
concat_df = pd.concat([train_target, test], ignore_index=True)
print(concat_df.shape)
concat_df.head()

(3980, 59)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00008ff9                      Fall                5                0   
1  000fd460                    Summer                9                0   
2  00105258                    Summer               10                1   
3  00115b9f                    Winter                9                0   
4  0016bb22                    Spring               18                1   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0      Winter             51.0            Fall     16.877316             46.0   
1         NaN              NaN            Fall     14.035590             48.0   
2        Fall             71.0            Fall     16.648696             56.5   
3        Fall             71.0          Summer     18.292347             56.0   
4      Summer              NaN             NaN           NaN              NaN   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             50.8                           NaN                    NaN   
1             46.0                          22.0                   75.0   
2             75.6                           NaN                   65.0   
3             81.6                           NaN                   60.0   
4              NaN                           NaN                    NaN   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                 NaN                   NaN                      NaN   
1                70.0                 122.0                      NaN   
2                94.0                 117.0                     Fall   
3                97.0                 117.0                   Summer   
4                 NaN                   NaN                      NaN   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          5.0                          7.0   
3                          6.0                          9.0   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                         NaN       Fall         0.0              0.0   
1                         NaN       Fall         3.0              0.0   
2                        33.0       Fall        20.0              1.0   
3                        37.0     Summer        18.0              1.0   
4                         NaN        NaN         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         0.0   
1           NaN                NaN          NaN               NaN         5.0   
2          10.2                1.0         14.7               2.0         7.0   
3           NaN                NaN          NaN               NaN         5.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          6.0   
1              0.0         11.0               1.0         11.0   
2              1.0         10.0               1.0         10.0   
3              0.0          7.0               0.0          7.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         6.0              1.0       Fall   
1               1.0         3.0              0.0     Winter   
2               1.0         5.0              0.0        NaN   
3               0.0         7.0              1.0     Summer   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         2.0     

In [15]:
concat_df['total_num_nan'] = concat_df.isna().sum(axis=1)

In [16]:
concat_df['total_num_nan'].describe()

count    3980.000000
mean       26.142462
std        17.257902
min         3.000000
25%         9.000000
50%        24.000000
75%        41.000000
max        55.000000
Name: total_num_nan, dtype: float64

In [17]:
nan_df = concat_df[concat_df['total_num_nan'] == concat_df['total_num_nan'].max()]
print(nan_df.shape)
nan_df.head()

(199, 60)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
42   023e1b6a                    Summer               13                0   
67   040d103f                    Spring                8                1   
84   04ccb838                    Summer                7                0   
107  05dc60ef                    Spring               12                1   
148  0882b065                    Summer               11                0   

    CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  \
42          NaN              NaN             NaN           NaN   
67          NaN              NaN             NaN           NaN   
84          NaN              NaN             NaN           NaN   
107         NaN              NaN             NaN           NaN   
148         NaN              NaN             NaN           NaN   

     Physical-Height  Physical-Weight  Physical-Waist_Circumference  \
42               NaN              NaN                           NaN   
67               NaN              NaN                           NaN   
84               NaN              NaN                           NaN   
107              NaN              NaN                           NaN   
148              NaN              NaN                           NaN   

     Physical-Diastolic_BP  Physical-HeartRate  Physical-Systolic_BP  \
42                     NaN                 NaN                   NaN   
67                     NaN                 NaN                   NaN   
84                     NaN                 NaN                   NaN   
107                    NaN                 NaN                   NaN   
148                    NaN                 NaN                   NaN   

    Fitness_Endurance-Season  Fitness_Endurance-Max_Stage  \
42                       NaN                          NaN   
67                       NaN                          NaN   
84                       NaN                          NaN   
107                      NaN                          NaN   
148                      NaN                          NaN   

     Fitness_Endurance-Time_Mins  Fitness_Endurance-Time_Sec FGC-Season  \
42                           NaN                         NaN        NaN   
67                           NaN                         NaN        NaN   
84                           NaN                         NaN        NaN   
107                          NaN                         NaN        NaN   
148                          NaN                         NaN        NaN   

     FGC-FGC_CU  FGC-FGC_CU_Zone  FGC-FGC_GSND  FGC-FGC_GSND_Zone  \
42          NaN              NaN           NaN                NaN   
67          NaN              NaN           NaN                NaN   
84          NaN              NaN           NaN                NaN   
107         NaN              NaN           NaN                NaN   
148         NaN              NaN           NaN                NaN   

     FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  FGC-FGC_PU_Zone  FGC-FGC_SRL  \
42           NaN               NaN         NaN              NaN          NaN   
67           NaN               NaN         NaN              NaN          NaN   
84           NaN               NaN         NaN              NaN          NaN   
107          NaN               NaN         NaN              NaN          NaN   
148          NaN               NaN         NaN              NaN          NaN   

     FGC-FGC_SRL_Zone  FGC-FGC_SRR  FGC-FGC_SRR_Zone  FGC-FGC_TL  \
42                NaN          NaN               NaN         NaN   
67                NaN          NaN               NaN         NaN   
84                NaN          NaN               NaN         NaN   
107               NaN          NaN               NaN         NaN   
148               NaN          NaN               NaN         NaN   

     FGC-FGC_TL_Zone BIA-Season  BIA-BIA_Activity_Level_num  BIA-BIA_BMC  \
42               NaN        NaN                         NaN          NaN   
67              

In [18]:
for col in concat_df.columns:
    if col == 'id':
        continue
    new_col_name = col + '_isnan'
    concat_df[new_col_name] = concat_df[col].isna().astype(int)

In [19]:
print(concat_df.shape)
concat_df.head()

(3980, 119)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00008ff9                      Fall                5                0   
1  000fd460                    Summer                9                0   
2  00105258                    Summer               10                1   
3  00115b9f                    Winter                9                0   
4  0016bb22                    Spring               18                1   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0      Winter             51.0            Fall     16.877316             46.0   
1         NaN              NaN            Fall     14.035590             48.0   
2        Fall             71.0            Fall     16.648696             56.5   
3        Fall             71.0          Summer     18.292347             56.0   
4      Summer              NaN             NaN           NaN              NaN   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             50.8                           NaN                    NaN   
1             46.0                          22.0                   75.0   
2             75.6                           NaN                   65.0   
3             81.6                           NaN                   60.0   
4              NaN                           NaN                    NaN   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                 NaN                   NaN                      NaN   
1                70.0                 122.0                      NaN   
2                94.0                 117.0                     Fall   
3                97.0                 117.0                   Summer   
4                 NaN                   NaN                      NaN   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          5.0                          7.0   
3                          6.0                          9.0   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                         NaN       Fall         0.0              0.0   
1                         NaN       Fall         3.0              0.0   
2                        33.0       Fall        20.0              1.0   
3                        37.0     Summer        18.0              1.0   
4                         NaN        NaN         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         0.0   
1           NaN                NaN          NaN               NaN         5.0   
2          10.2                1.0         14.7               2.0         7.0   
3           NaN                NaN          NaN               NaN         5.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          6.0   
1              0.0         11.0               1.0         11.0   
2              1.0         10.0               1.0         10.0   
3              0.0          7.0               0.0          7.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         6.0              1.0       Fall   
1               1.0         3.0              0.0     Winter   
2               1.0         5.0              0.0        NaN   
3               0.0         7.0              1.0     Summer   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         2.0     

In [20]:
instruments = data_dict['Instrument'].unique().tolist()
instruments.remove('Identifier')
print(len(instruments))
instruments

11


['Demographics',
 "Children's Global Assessment Scale",
 'Physical Measures',
 'FitnessGram Vitals and Treadmill',
 'FitnessGram Child',
 'Bio-electric Impedance Analysis',
 'Physical Activity Questionnaire (Adolescents)',
 'Physical Activity Questionnaire (Children)',
 'Parent-Child Internet Addiction Test',
 'Sleep Disturbance Scale',
 'Internet Use']

In [21]:
for instrument in instruments:
    if 'Parent-Child Internet Addiction Test' == instrument:
        continue
    instrument_df = data_dict[data_dict['Instrument'] == instrument]
    field_list = instrument_df['Field'].unique().tolist()
    concat_df[instrument + '_num_nan'] = concat_df[field_list].isna().sum(axis=1)    

In [22]:
print(concat_df.shape)
concat_df.head()

(3980, 129)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00008ff9                      Fall                5                0   
1  000fd460                    Summer                9                0   
2  00105258                    Summer               10                1   
3  00115b9f                    Winter                9                0   
4  0016bb22                    Spring               18                1   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0      Winter             51.0            Fall     16.877316             46.0   
1         NaN              NaN            Fall     14.035590             48.0   
2        Fall             71.0            Fall     16.648696             56.5   
3        Fall             71.0          Summer     18.292347             56.0   
4      Summer              NaN             NaN           NaN              NaN   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             50.8                           NaN                    NaN   
1             46.0                          22.0                   75.0   
2             75.6                           NaN                   65.0   
3             81.6                           NaN                   60.0   
4              NaN                           NaN                    NaN   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                 NaN                   NaN                      NaN   
1                70.0                 122.0                      NaN   
2                94.0                 117.0                     Fall   
3                97.0                 117.0                   Summer   
4                 NaN                   NaN                      NaN   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          5.0                          7.0   
3                          6.0                          9.0   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                         NaN       Fall         0.0              0.0   
1                         NaN       Fall         3.0              0.0   
2                        33.0       Fall        20.0              1.0   
3                        37.0     Summer        18.0              1.0   
4                         NaN        NaN         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         0.0   
1           NaN                NaN          NaN               NaN         5.0   
2          10.2                1.0         14.7               2.0         7.0   
3           NaN                NaN          NaN               NaN         5.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          6.0   
1              0.0         11.0               1.0         11.0   
2              1.0         10.0               1.0         10.0   
3              0.0          7.0               0.0          7.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         6.0              1.0       Fall   
1               1.0         3.0              0.0     Winter   
2               1.0         5.0              0.0        NaN   
3               0.0         7.0              1.0     Summer   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         2.0     

In [23]:
train_parquet_id_folders_list = os.listdir(path + 'series_train.parquet/')
print(len(train_parquet_id_folders_list))
train_parquet_id_folders_list

996


['id=00115b9f',
 'id=001f3379',
 'id=00f332d1',
 'id=01085eb3',
 'id=012cadd8',
 'id=012e3869',
 'id=029a19c9',
 'id=02cebf33',
 'id=02cf7384',
 'id=035c96dd',
 'id=03a9019b',
 'id=0417c91e',
 'id=045a0a94',
 'id=04afb6f9',
 'id=04bb1a76',
 'id=04cb2c30',
 'id=04d06a9c',
 'id=04f094a8',
 'id=051680a0',
 'id=055156e2',
 'id=059eed01',
 'id=05bbed1b',
 'id=05db1b9b',
 'id=05e94f88',
 'id=063b16fc',
 'id=064e8da5',
 'id=0668373f',
 'id=067b9287',
 'id=06c8b2fb',
 'id=06eb8adb',
 'id=070386b2',
 'id=07048067',
 'id=0720320e',
 'id=0745c390',
 'id=080698b7',
 'id=082df556',
 'id=08577722',
 'id=08660d12',
 'id=089a6b19',
 'id=09331bb8',
 'id=0983654b',
 'id=099e3614',
 'id=09b29113',
 'id=0a418b57',
 'id=0a431608',
 'id=0b4014f0',
 'id=0b50f3fa',
 'id=0b518637',
 'id=0b7d7aec',
 'id=0b7d9da6',
 'id=0bd89878',
 'id=0bfe4fc9',
 'id=0c4e2d68',
 'id=0c4eabac',
 'id=0c98f822',
 'id=0cbe4e54',
 'id=0d01bbf2',
 'id=0d279d77',
 'id=0d4800c8',
 'id=0d4fa8f4',
 'id=0d570d3e',
 'id=0d924604',
 'id=0e3

In [24]:
train_parquet_id_list = [v.replace('id=', '') for v in train_parquet_id_folders_list]
print(len(train_parquet_id_list))
train_parquet_id_list

996


['00115b9f',
 '001f3379',
 '00f332d1',
 '01085eb3',
 '012cadd8',
 '012e3869',
 '029a19c9',
 '02cebf33',
 '02cf7384',
 '035c96dd',
 '03a9019b',
 '0417c91e',
 '045a0a94',
 '04afb6f9',
 '04bb1a76',
 '04cb2c30',
 '04d06a9c',
 '04f094a8',
 '051680a0',
 '055156e2',
 '059eed01',
 '05bbed1b',
 '05db1b9b',
 '05e94f88',
 '063b16fc',
 '064e8da5',
 '0668373f',
 '067b9287',
 '06c8b2fb',
 '06eb8adb',
 '070386b2',
 '07048067',
 '0720320e',
 '0745c390',
 '080698b7',
 '082df556',
 '08577722',
 '08660d12',
 '089a6b19',
 '09331bb8',
 '0983654b',
 '099e3614',
 '09b29113',
 '0a418b57',
 '0a431608',
 '0b4014f0',
 '0b50f3fa',
 '0b518637',
 '0b7d7aec',
 '0b7d9da6',
 '0bd89878',
 '0bfe4fc9',
 '0c4e2d68',
 '0c4eabac',
 '0c98f822',
 '0cbe4e54',
 '0d01bbf2',
 '0d279d77',
 '0d4800c8',
 '0d4fa8f4',
 '0d570d3e',
 '0d924604',
 '0e3b0bd2',
 '0ec403df',
 '0ed2a3c8',
 '0eddd8e5',
 '0f6b71c4',
 '0fbb3ca5',
 '101774f0',
 '101c27f1',
 '108b8659',
 '10ad8c48',
 '10e46254',
 '113f5798',
 '11739de2',
 '119d7562',
 '119e181e',

In [25]:
test_parquet_id_folders_list = os.listdir(path + 'series_test.parquet/')
print(len(test_parquet_id_folders_list))
test_parquet_id_folders_list

2


['id=00115b9f', 'id=001f3379']

In [26]:
test_parquet_id_list = [v.replace('id=', '') for v in test_parquet_id_folders_list]
print(len(test_parquet_id_list))
test_parquet_id_list

2


['00115b9f', '001f3379']

In [27]:
train_temp_df = concat_df.head(train.shape[0])
print(train_temp_df.shape)
train_temp_df.head()

(3960, 129)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00008ff9                      Fall                5                0   
1  000fd460                    Summer                9                0   
2  00105258                    Summer               10                1   
3  00115b9f                    Winter                9                0   
4  0016bb22                    Spring               18                1   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0      Winter             51.0            Fall     16.877316             46.0   
1         NaN              NaN            Fall     14.035590             48.0   
2        Fall             71.0            Fall     16.648696             56.5   
3        Fall             71.0          Summer     18.292347             56.0   
4      Summer              NaN             NaN           NaN              NaN   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             50.8                           NaN                    NaN   
1             46.0                          22.0                   75.0   
2             75.6                           NaN                   65.0   
3             81.6                           NaN                   60.0   
4              NaN                           NaN                    NaN   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                 NaN                   NaN                      NaN   
1                70.0                 122.0                      NaN   
2                94.0                 117.0                     Fall   
3                97.0                 117.0                   Summer   
4                 NaN                   NaN                      NaN   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          5.0                          7.0   
3                          6.0                          9.0   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                         NaN       Fall         0.0              0.0   
1                         NaN       Fall         3.0              0.0   
2                        33.0       Fall        20.0              1.0   
3                        37.0     Summer        18.0              1.0   
4                         NaN        NaN         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         0.0   
1           NaN                NaN          NaN               NaN         5.0   
2          10.2                1.0         14.7               2.0         7.0   
3           NaN                NaN          NaN               NaN         5.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          6.0   
1              0.0         11.0               1.0         11.0   
2              1.0         10.0               1.0         10.0   
3              0.0          7.0               0.0          7.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         6.0              1.0       Fall   
1               1.0         3.0              0.0     Winter   
2               1.0         5.0              0.0        NaN   
3               0.0         7.0              1.0     Summer   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         2.0     

In [28]:
test_temp_df = concat_df.tail(test.shape[0])
print(test_temp_df.shape)
test_temp_df.head()

(20, 129)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
3960  00008ff9                      Fall                5                0   
3961  000fd460                    Summer                9                0   
3962  00105258                    Summer               10                1   
3963  00115b9f                    Winter                9                0   
3964  0016bb22                    Spring               18                1   

     CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  \
3960      Winter             51.0            Fall     16.877316   
3961         NaN              NaN            Fall     14.035590   
3962        Fall             71.0            Fall     16.648696   
3963        Fall             71.0          Summer     18.292347   
3964      Summer              NaN             NaN           NaN   

      Physical-Height  Physical-Weight  Physical-Waist_Circumference  \
3960             46.0             50.8                           NaN   
3961             48.0             46.0                          22.0   
3962             56.5             75.6                           NaN   
3963             56.0             81.6                           NaN   
3964              NaN              NaN                           NaN   

      Physical-Diastolic_BP  Physical-HeartRate  Physical-Systolic_BP  \
3960                    NaN                 NaN                   NaN   
3961                   75.0                70.0                 122.0   
3962                   65.0                94.0                 117.0   
3963                   60.0                97.0                 117.0   
3964                    NaN                 NaN                   NaN   

     Fitness_Endurance-Season  Fitness_Endurance-Max_Stage  \
3960                      NaN                          NaN   
3961                      NaN                          NaN   
3962                     Fall                          5.0   
3963                   Summer                          6.0   
3964                      NaN                          NaN   

      Fitness_Endurance-Time_Mins  Fitness_Endurance-Time_Sec FGC-Season  \
3960                          NaN                         NaN       Fall   
3961                          NaN                         NaN       Fall   
3962                          7.0                        33.0       Fall   
3963                          9.0                        37.0     Summer   
3964                          NaN                         NaN        NaN   

      FGC-FGC_CU  FGC-FGC_CU_Zone  FGC-FGC_GSND  FGC-FGC_GSND_Zone  \
3960         0.0              0.0           NaN                NaN   
3961         3.0              0.0           NaN                NaN   
3962        20.0              1.0          10.2                1.0   
3963        18.0              1.0           NaN                NaN   
3964         NaN              NaN           NaN                NaN   

      FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  FGC-FGC_PU_Zone  FGC-FGC_SRL  \
3960          NaN               NaN         0.0              0.0          7.0   
3961          NaN               NaN         5.0              0.0         11.0   
3962         14.7               2.0         7.0              1.0         10.0   
3963          NaN               NaN         5.0              0.0          7.0   
3964          NaN               NaN         NaN              NaN          NaN   

      FGC-FGC_SRL_Zone  FGC-FGC_SRR  FGC-FGC_SRR_Zone  FGC-FGC_TL  \
3960               0.0          6.0               0.0         6.0   
3961               1.0         11.0               1.0         3.0   
3962               1.0         10.0               1.0         5.0   
3963               0.0          7.0               0.0         7.0   
3964               NaN          NaN               NaN         NaN   

      FGC-FGC_TL_Zone BIA-Season  BIA-BIA_Activity_Level_num  BIA-BIA_BMC  \
3960              1.0       Fall      

In [29]:
train_temp_df['has_parquet'] = train_temp_df['id'].isin(train_parquet_id_list).astype(int)
print(train_temp_df.shape)
train_temp_df.head()

(3960, 130)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00008ff9                      Fall                5                0   
1  000fd460                    Summer                9                0   
2  00105258                    Summer               10                1   
3  00115b9f                    Winter                9                0   
4  0016bb22                    Spring               18                1   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0      Winter             51.0            Fall     16.877316             46.0   
1         NaN              NaN            Fall     14.035590             48.0   
2        Fall             71.0            Fall     16.648696             56.5   
3        Fall             71.0          Summer     18.292347             56.0   
4      Summer              NaN             NaN           NaN              NaN   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             50.8                           NaN                    NaN   
1             46.0                          22.0                   75.0   
2             75.6                           NaN                   65.0   
3             81.6                           NaN                   60.0   
4              NaN                           NaN                    NaN   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                 NaN                   NaN                      NaN   
1                70.0                 122.0                      NaN   
2                94.0                 117.0                     Fall   
3                97.0                 117.0                   Summer   
4                 NaN                   NaN                      NaN   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          5.0                          7.0   
3                          6.0                          9.0   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                         NaN       Fall         0.0              0.0   
1                         NaN       Fall         3.0              0.0   
2                        33.0       Fall        20.0              1.0   
3                        37.0     Summer        18.0              1.0   
4                         NaN        NaN         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         0.0   
1           NaN                NaN          NaN               NaN         5.0   
2          10.2                1.0         14.7               2.0         7.0   
3           NaN                NaN          NaN               NaN         5.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          6.0   
1              0.0         11.0               1.0         11.0   
2              1.0         10.0               1.0         10.0   
3              0.0          7.0               0.0          7.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         6.0              1.0       Fall   
1               1.0         3.0              0.0     Winter   
2               1.0         5.0              0.0        NaN   
3               0.0         7.0              1.0     Summer   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         2.0     

In [30]:
test_temp_df['has_parquet'] = test_temp_df['id'].isin(test_parquet_id_list).astype(int)
print(test_temp_df.shape)
test_temp_df.head()

(20, 130)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
3960  00008ff9                      Fall                5                0   
3961  000fd460                    Summer                9                0   
3962  00105258                    Summer               10                1   
3963  00115b9f                    Winter                9                0   
3964  0016bb22                    Spring               18                1   

     CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  \
3960      Winter             51.0            Fall     16.877316   
3961         NaN              NaN            Fall     14.035590   
3962        Fall             71.0            Fall     16.648696   
3963        Fall             71.0          Summer     18.292347   
3964      Summer              NaN             NaN           NaN   

      Physical-Height  Physical-Weight  Physical-Waist_Circumference  \
3960             46.0             50.8                           NaN   
3961             48.0             46.0                          22.0   
3962             56.5             75.6                           NaN   
3963             56.0             81.6                           NaN   
3964              NaN              NaN                           NaN   

      Physical-Diastolic_BP  Physical-HeartRate  Physical-Systolic_BP  \
3960                    NaN                 NaN                   NaN   
3961                   75.0                70.0                 122.0   
3962                   65.0                94.0                 117.0   
3963                   60.0                97.0                 117.0   
3964                    NaN                 NaN                   NaN   

     Fitness_Endurance-Season  Fitness_Endurance-Max_Stage  \
3960                      NaN                          NaN   
3961                      NaN                          NaN   
3962                     Fall                          5.0   
3963                   Summer                          6.0   
3964                      NaN                          NaN   

      Fitness_Endurance-Time_Mins  Fitness_Endurance-Time_Sec FGC-Season  \
3960                          NaN                         NaN       Fall   
3961                          NaN                         NaN       Fall   
3962                          7.0                        33.0       Fall   
3963                          9.0                        37.0     Summer   
3964                          NaN                         NaN        NaN   

      FGC-FGC_CU  FGC-FGC_CU_Zone  FGC-FGC_GSND  FGC-FGC_GSND_Zone  \
3960         0.0              0.0           NaN                NaN   
3961         3.0              0.0           NaN                NaN   
3962        20.0              1.0          10.2                1.0   
3963        18.0              1.0           NaN                NaN   
3964         NaN              NaN           NaN                NaN   

      FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  FGC-FGC_PU_Zone  FGC-FGC_SRL  \
3960          NaN               NaN         0.0              0.0          7.0   
3961          NaN               NaN         5.0              0.0         11.0   
3962         14.7               2.0         7.0              1.0         10.0   
3963          NaN               NaN         5.0              0.0          7.0   
3964          NaN               NaN         NaN              NaN          NaN   

      FGC-FGC_SRL_Zone  FGC-FGC_SRR  FGC-FGC_SRR_Zone  FGC-FGC_TL  \
3960               0.0          6.0               0.0         6.0   
3961               1.0         11.0               1.0         3.0   
3962               1.0         10.0               1.0         5.0   
3963               0.0          7.0               0.0         7.0   
3964               NaN          NaN               NaN         NaN   

      FGC-FGC_TL_Zone BIA-Season  BIA-BIA_Activity_Level_num  BIA-BIA_BMC  \
3960              1.0       Fall      

In [31]:
# https://www.kaggle.com/code/antoninadolgorukova/cmi-piu-actigraphy-data-eda
entropy = lambda x: -(x / x.sum() * np.log(x / x.sum() + 1e-9)).sum()

In [32]:
def feat_engi(df, target_cols):
    stats_df = df[target_cols].describe(percentiles=[0.01, 0.03] + [(i+1)*0.05 for i in range(19)] + [0.97, 0.99]).T
    count = stats_df['count'][0]
    stats_df.drop('count', axis=1, inplace=True)
    
    column_names_list = []
    for idx in stats_df.index:
        for col in stats_df.columns:
            column_names_list.append(str(idx) + '_' + str(col))

    reshaped_df = pd.DataFrame(stats_df.values.reshape(-1)).T.reset_index(drop=True)
    reshaped_df.columns = column_names_list

    reshaped_df['count'] = count

    return reshaped_df

In [33]:
def groupby_feat_engi(df, col_to_group, target_col):
    stats_df = pd.DataFrame(
        df.groupby(col_to_group)[target_col].describe(percentiles=[0.01, 0.03] + [(i+1)*0.05 for i in range(19)] + [0.97, 0.99])
    )

    stats_df['sum'] = df.groupby(col_to_group)[target_col].sum()
    stats_df['entropy'] = df.groupby(col_to_group)[target_col].apply(entropy)
    
    column_names_list = []
    for idx in stats_df.index:
        for col in stats_df.columns:
            column_names_list.append(target_col + '_' + col_to_group + '_' + str(idx) + '_' + str(col))

    reshaped_df = pd.DataFrame(stats_df.values.reshape(-1)).T.reset_index(drop=True)
    reshaped_df.columns = column_names_list

    return reshaped_df

In [34]:
def uncommon_groupby_feat_engi(df, col_to_group, target_col):
    stats_df = pd.DataFrame(
        df.groupby(col_to_group)[target_col].describe(percentiles=[0.01, 0.03] + [(i+1)*0.05 for i in range(19)] + [0.97, 0.99])
    )

    stats_df['sum'] = df.groupby(col_to_group)[target_col].sum()
    stats_df['entropy'] = df.groupby(col_to_group)[target_col].apply(entropy)

    
    stats_stats_df = stats_df.describe(percentiles=[0.01, 0.03] + [(i+1)*0.05 for i in range(19)] + [0.97, 0.99])
    stats_stats_count = stats_stats_df['count'][0]
    stats_stats_df.drop('count', axis=0, inplace=True)
    stats_stats_df = stats_stats_df.T
    
    column_names_list = []
    for idx in stats_stats_df.index:
        for col in stats_stats_df.columns:
            column_names_list.append(target_col + '_' + col_to_group + '_' + str(idx) + '_' + str(col))
    
    reshaped_df = pd.DataFrame(stats_stats_df.values.reshape(-1)).T.reset_index(drop=True)
    reshaped_df.columns = column_names_list

    current_cols = reshaped_df.columns.tolist()
    count_col_name = target_col + '_' + col_to_group + '_count'
    reshaped_df[count_col_name] = stats_stats_count

    reshaped_df = reshaped_df[[count_col_name] + current_cols]

    return reshaped_df

In [35]:
def read_parquet(dataset='train'):
    parquet_id_folders_list = os.listdir(path + 'series_' + dataset + '.parquet/')
    ts_list = []
    ts_features_list = []
    for id_folder in tqdm(parquet_id_folders_list):
        iid = id_folder.replace('id=', '')
    
        parquet_files_path = path + 'series_' + dataset + '.parquet/' + id_folder + '/'
        parquet_files_list = os.listdir(parquet_files_path)
    
        dfs_list = []
        for parquet_filename in parquet_files_list:
            if '.parquet' in parquet_filename:
                parquet_df = pd.read_parquet(parquet_files_path + parquet_filename)
                dfs_list.append(parquet_df)
        parquet_concat_df = pd.concat(dfs_list, ignore_index=True)
        current_cols = parquet_concat_df.columns.tolist()
        
        parquet_concat_df['id'] = iid
        
        parquet_concat_df = parquet_concat_df[['id'] + current_cols]
        
        parquet_concat_df['day_since_wear'] = (parquet_concat_df['relative_date_PCIAT'] - parquet_concat_df['relative_date_PCIAT'].min()).astype(int)
        parquet_concat_df['time_of_day_sec'] = parquet_concat_df['time_of_day'] / 1e9
        parquet_concat_df.drop('time_of_day', axis=1, inplace=True)
        parquet_concat_df['time_of_day_min'] = parquet_concat_df['time_of_day_sec'] / 60
        parquet_concat_df['time_of_day_hour'] = parquet_concat_df['time_of_day_min'] / 60
        parquet_concat_df['time_of_day_day'] = parquet_concat_df['time_of_day_hour'] / 24
        parquet_concat_df['time_of_day_hour_window'] = parquet_concat_df['time_of_day_hour'].astype(int)
        parquet_concat_df['time_of_day_min_window'] = parquet_concat_df['time_of_day_min'].astype(int)
        parquet_concat_df['time_of_day_15_min_window'] = (parquet_concat_df['time_of_day_min'] / 15).astype(int)
        parquet_concat_df['timestamp_day'] = parquet_concat_df['day_since_wear'] + parquet_concat_df['time_of_day_day']
    
        if parquet_concat_df['timestamp_day'].nunique() != parquet_concat_df.shape[0]:
            print('yes')
    
        parquet_concat_df['timestamp_hour'] = parquet_concat_df['timestamp_day'] * 24
        parquet_concat_df['timestamp_min'] = parquet_concat_df['timestamp_day'] * 24 * 60
        parquet_concat_df['timestamp_sec'] = parquet_concat_df['timestamp_day'] * 24 * 60 * 60
        parquet_concat_df['timestamp_15_min'] = parquet_concat_df['timestamp_day'] * 24 * (60/15)
    
        parquet_concat_df['timestamp_hour_window'] = parquet_concat_df['timestamp_hour'].astype(int)
        parquet_concat_df['timestamp_min_window'] = parquet_concat_df['timestamp_min'].astype(int)
        parquet_concat_df['timestamp_15_min_window'] = parquet_concat_df['timestamp_15_min'].astype(int)
    
        battery_voltage_start = parquet_concat_df['battery_voltage'][0]
        parquet_concat_df['battery_use_since_wear'] = -(parquet_concat_df['battery_voltage'] - battery_voltage_start)
        
    
        worn_df = parquet_concat_df[parquet_concat_df['non-wear_flag'] == 0].reset_index(drop=True)
    
        
        feature_cols = ['X', 'Y', 'Z', 'enmo', 'anglez', 'light', 'battery_use_since_wear']
    
        features_df = feat_engi(worn_df, feature_cols)
    
        groupby_cols = ['weekday', 'time_of_day_hour_window', 'time_of_day_15_min_window']
    
        groupby_df_list = []
        for groupby_col in groupby_cols:
            for feature_col in feature_cols:
                groupby_features_df = groupby_feat_engi(worn_df, groupby_col, feature_col)
                groupby_df_list.append(groupby_features_df)
    
        groupby_concat_df = pd.concat(groupby_df_list, axis=1)
    
        uncommon_groupby_cols = ['day_since_wear', 'timestamp_hour_window', 'timestamp_15_min_window']#, 'timestamp_min_window']
    
        uncommon_groupby_df_list = []
        for uncommon_groupby_col in uncommon_groupby_cols:
            for unc_feature_col in feature_cols:
                uncommon_groupby_df = uncommon_groupby_feat_engi(worn_df, uncommon_groupby_col, unc_feature_col)
                uncommon_groupby_df_list.append(uncommon_groupby_df)
    
        features_concat_df = pd.concat([features_df, groupby_concat_df, uncommon_groupby_df], axis=1)
        features_current_cols = features_concat_df.columns.tolist()
        features_concat_df['id'] = iid
        features_concat_df = features_concat_df[['id'] + features_current_cols]
    
        for q in [1,2,3,4]:
            if q in worn_df['quarter'].tolist():
                features_concat_df['data_collected_in_quarter_' + str(q)] = 1
            else:
                features_concat_df['data_collected_in_quarter_' + str(q)] = 0

        features_concat_df['id'] = features_concat_df['id'].astype(str)

        features_concat_df.to_csv(path + 'series_' + dataset + '.parquet/id=' + iid + '/features.csv', index=False)
        
        ts_list.append(parquet_concat_df)
        ts_features_list.append(features_concat_df)
    return ts_list, ts_features_list

In [36]:
#train_ts_list, train_ts_features_list = read_parquet()

In [37]:
#test_ts_list, test_ts_features_list = read_parquet(dataset='test')

In [38]:
def read_features_files():
    temp_dfs_list = []
    for temp_id_folder in tqdm(train_parquet_id_folders_list):
        temp_files_list = os.listdir(path + 'series_train.parquet/' + temp_id_folder + '/')
        for temp_filename in temp_files_list:
            if '.csv' in temp_filename:
                temp_df = pd.read_csv(path + 'series_train.parquet/' + temp_id_folder + '/' + temp_filename, dtype={'id': str})
                temp_dfs_list.append(temp_df)

    return temp_dfs_list

In [39]:
train_ts_features_list = read_features_files()

100%|████████████████████████████████████████████████████████████████████████████████| 996/996 [18:36<00:00,  1.12s/it]


In [40]:
len(train_ts_features_list)

996

In [41]:
#len(test_ts_features_list)

In [42]:
train_ts_features_concat_df = pd.concat(train_ts_features_list, ignore_index=True)
print(train_ts_features_concat_df.shape)
train_ts_features_concat_df.head()

(996, 27676)


id    X_mean     X_std     X_min      X_1%      X_3%      X_5%  \
0  00115b9f -0.316384  0.453665 -1.746094 -0.957459 -0.934769 -0.914427   
1  001f3379  0.047271  0.610522 -1.038711 -0.987389 -0.965308 -0.929665   
2  00f332d1  0.239004  0.528992 -1.952594 -0.937417 -0.885141 -0.828783   
3  01085eb3 -0.363822  0.514492 -2.284304 -0.993339 -0.979900 -0.966016   
4  012cadd8  0.018670  0.595251 -2.143912 -0.977178 -0.942561 -0.915178   

      X_10%     X_15%     X_20%     X_25%     X_30%     X_35%     X_40%  \
0 -0.871721 -0.811414 -0.745521 -0.684180 -0.625026 -0.567314 -0.508016   
1 -0.822527 -0.744080 -0.624830 -0.482846 -0.376047 -0.219380 -0.053169   
2 -0.619099 -0.376297 -0.178431 -0.063253  0.013506  0.065460  0.143172   
3 -0.931370 -0.890299 -0.849929 -0.795286 -0.743438 -0.688371 -0.631032   
4 -0.813863 -0.722694 -0.592835 -0.514300 -0.408334 -0.309016 -0.184722   

      X_45%     X_50%     X_55%     X_60%     X_65%     X_70%     X_75%  \
0 -0.437547 -0.366849 -0.306484 -0.255599 -0.193461 -0.108544 -0.010677   
1 -0.040168  0.052813  0.158746  0.274674  0.387562  0.494733  0.597837   
2  0.218311  0.291499  0.377403  0.451753  0.535908  0.610236  0.685092   
3 -0.571515 -0.503552 -0.419841 -0.334197 -0.249098 -0.145403 -0.024163   
4 -0.056190  0.036376  0.143034  0.247260  0.360007  0.444944  0.539581   

      X_80%     X_85%     X_90%     X_95%     X_97%     X_99%     X_max  \
0  0.046125  0.138923  0.380755  0.540839  0.687074  0.889449  1.507865   
1  0.694278  0.786812  0.862478  0.947284  0.978612  0.996103  1.034351   
2  0.752594  0.816693  0.886523  0.950107  0.974539  0.996652  1.666465   
3  0.140853  0.273915  0.454001  0.632677  0.766140  0.891769  1.000692   
4  0.634786  0.732723  0.825133  0.917491  0.953949  0.993068  3.341210   

     Y_mean     Y_std     Y_min      Y_1%      Y_3%      Y_5%     Y_10%  \
0  0.016009  0.502702 -2.905339 -0.977749 -0.928411 -0.877531 -0.730302   
1 -0.003308  0.454752 -1.522690 -0.897626 -0.823287 -0.765601 -0.611894   
2  0.067278  0.488057 -2.361866 -0.969803 -0.935022 -0.897576 -0.716495   
3 -0.057915  0.431997 -2.276082 -0.989564 -0.930472 -0.851888 -0.673733   
4  0.071660  0.508311 -3.373025 -1.048439 -0.918585 -0.826581 -0.649036   

      Y_15%     Y_20%     Y_25%     Y_30%     Y_35%     Y_40%     Y_45%  \
0 -0.584147 -0.430516 -0.309863 -0.224424 -0.136134 -0.054089 -0.010130   
1 -0.491171 -0.407455 -0.309514 -0.225133 -0.148145 -0.090263 -0.044995   
2 -0.487230 -0.318040 -0.211965 -0.118938 -0.036678  0.012682  0.064731   
3 -0.518658 -0.412982 -0.324336 -0.251998 -0.187119 -0.134176 -0.082795   
4 -0.480292 -0.346330 -0.254007 -0.181510 -0.096670 -0.036464  0.019013   

      Y_50%     Y_55%     Y_60%     Y_65%     Y_70%     Y_75%     Y_80%  \
0  0.024974  0.068776  0.122630  0.205260  0.309391  0.400677  0.495396   
1 -0.032031  0.017075  0.052635  0.125170  0.184959  0.257940  0.360792   
2  0.109878  0.157751  0.212424  0.272188  0.338519  0.400713  0.471606   
3 -0.034986  0.006740  0.053148  0.100025  0.154695  0.219121  0.291143   
4  0.096187  0.183083  0.233549  0.294277  0.357776  0.458349  0.544063   

      Y_85%     Y_90%     Y_95%     Y_97%     Y_99%     Y_max    Z_mean  \
0  0.593706  0.702779  0.812206  0.858177  0.934910  1.666354 -0.167890   
1  0.499812  0.678877  0.834630  0.907865  0.986683  1.946303  0.043286   
2  0.561150  0.691220  0.843300  0.909164  0.969124  1.016429  0.343440   
3  0.380603  0.501571  0.670905  0.757785  0.898741  1.011419 -0.300906   
4  0.634750  0.711058  0.828655  0.895826  0.972946  4.442658 -0.061682   

      Z_std     Z_min      Z_1%      Z_3%      Z_5%     Z_10%     Z_15%  \
0  0.585710 -1.048372 -1.010391 -0.993666 -0.957112 -0.897970 -0.821275   
1  0.623933 -1.018787 -1.009865 -1.008992 -1.007377 -0.944074 -0.788080   
2  0.515729 -1.016758 -0.988789 -0.857476 -0.733482 -0.457626 -0.252333   
3  0.520138 -1.022549 -0.987087 -0.970566 -0.954552 -0.915447 -0.871919   
4  0.578022 -1.003249 -0.9

In [43]:
'''test_ts_features_concat_df = pd.concat(test_ts_features_list, ignore_index=True)
print(test_ts_features_concat_df.shape)
test_ts_features_concat_df.head()'''

'test_ts_features_concat_df = pd.concat(test_ts_features_list, ignore_index=True)\nprint(test_ts_features_concat_df.shape)\ntest_ts_features_concat_df.head()'

In [44]:
train_ts_features_concat_df['id'].isin(train_parquet_id_list).sum()

996

In [45]:
#test_ts_features_concat_df['id'].isin(test_parquet_id_list).sum()

In [46]:
def remove_useless_cols(df):
    describe_df = df.describe()

    cols_to_drop = []
    for col in tqdm(describe_df.columns):
        if describe_df[col]['std'] == 0:
            cols_to_drop.append(col)

    print(len(cols_to_drop))
    
    df.drop(cols_to_drop, axis=1, inplace=True)

    return df

In [47]:
train_ts_features_concat_df = remove_useless_cols(train_ts_features_concat_df)
print(train_ts_features_concat_df.shape)
train_ts_features_concat_df.head()

100%|█████████████████████████████████████████████████████████████████████████| 27675/27675 [00:00<00:00, 75710.54it/s]


1
(996, 27675)


id    X_mean     X_std     X_min      X_1%      X_3%      X_5%  \
0  00115b9f -0.316384  0.453665 -1.746094 -0.957459 -0.934769 -0.914427   
1  001f3379  0.047271  0.610522 -1.038711 -0.987389 -0.965308 -0.929665   
2  00f332d1  0.239004  0.528992 -1.952594 -0.937417 -0.885141 -0.828783   
3  01085eb3 -0.363822  0.514492 -2.284304 -0.993339 -0.979900 -0.966016   
4  012cadd8  0.018670  0.595251 -2.143912 -0.977178 -0.942561 -0.915178   

      X_10%     X_15%     X_20%     X_25%     X_30%     X_35%     X_40%  \
0 -0.871721 -0.811414 -0.745521 -0.684180 -0.625026 -0.567314 -0.508016   
1 -0.822527 -0.744080 -0.624830 -0.482846 -0.376047 -0.219380 -0.053169   
2 -0.619099 -0.376297 -0.178431 -0.063253  0.013506  0.065460  0.143172   
3 -0.931370 -0.890299 -0.849929 -0.795286 -0.743438 -0.688371 -0.631032   
4 -0.813863 -0.722694 -0.592835 -0.514300 -0.408334 -0.309016 -0.184722   

      X_45%     X_50%     X_55%     X_60%     X_65%     X_70%     X_75%  \
0 -0.437547 -0.366849 -0.306484 -0.255599 -0.193461 -0.108544 -0.010677   
1 -0.040168  0.052813  0.158746  0.274674  0.387562  0.494733  0.597837   
2  0.218311  0.291499  0.377403  0.451753  0.535908  0.610236  0.685092   
3 -0.571515 -0.503552 -0.419841 -0.334197 -0.249098 -0.145403 -0.024163   
4 -0.056190  0.036376  0.143034  0.247260  0.360007  0.444944  0.539581   

      X_80%     X_85%     X_90%     X_95%     X_97%     X_99%     X_max  \
0  0.046125  0.138923  0.380755  0.540839  0.687074  0.889449  1.507865   
1  0.694278  0.786812  0.862478  0.947284  0.978612  0.996103  1.034351   
2  0.752594  0.816693  0.886523  0.950107  0.974539  0.996652  1.666465   
3  0.140853  0.273915  0.454001  0.632677  0.766140  0.891769  1.000692   
4  0.634786  0.732723  0.825133  0.917491  0.953949  0.993068  3.341210   

     Y_mean     Y_std     Y_min      Y_1%      Y_3%      Y_5%     Y_10%  \
0  0.016009  0.502702 -2.905339 -0.977749 -0.928411 -0.877531 -0.730302   
1 -0.003308  0.454752 -1.522690 -0.897626 -0.823287 -0.765601 -0.611894   
2  0.067278  0.488057 -2.361866 -0.969803 -0.935022 -0.897576 -0.716495   
3 -0.057915  0.431997 -2.276082 -0.989564 -0.930472 -0.851888 -0.673733   
4  0.071660  0.508311 -3.373025 -1.048439 -0.918585 -0.826581 -0.649036   

      Y_15%     Y_20%     Y_25%     Y_30%     Y_35%     Y_40%     Y_45%  \
0 -0.584147 -0.430516 -0.309863 -0.224424 -0.136134 -0.054089 -0.010130   
1 -0.491171 -0.407455 -0.309514 -0.225133 -0.148145 -0.090263 -0.044995   
2 -0.487230 -0.318040 -0.211965 -0.118938 -0.036678  0.012682  0.064731   
3 -0.518658 -0.412982 -0.324336 -0.251998 -0.187119 -0.134176 -0.082795   
4 -0.480292 -0.346330 -0.254007 -0.181510 -0.096670 -0.036464  0.019013   

      Y_50%     Y_55%     Y_60%     Y_65%     Y_70%     Y_75%     Y_80%  \
0  0.024974  0.068776  0.122630  0.205260  0.309391  0.400677  0.495396   
1 -0.032031  0.017075  0.052635  0.125170  0.184959  0.257940  0.360792   
2  0.109878  0.157751  0.212424  0.272188  0.338519  0.400713  0.471606   
3 -0.034986  0.006740  0.053148  0.100025  0.154695  0.219121  0.291143   
4  0.096187  0.183083  0.233549  0.294277  0.357776  0.458349  0.544063   

      Y_85%     Y_90%     Y_95%     Y_97%     Y_99%     Y_max    Z_mean  \
0  0.593706  0.702779  0.812206  0.858177  0.934910  1.666354 -0.167890   
1  0.499812  0.678877  0.834630  0.907865  0.986683  1.946303  0.043286   
2  0.561150  0.691220  0.843300  0.909164  0.969124  1.016429  0.343440   
3  0.380603  0.501571  0.670905  0.757785  0.898741  1.011419 -0.300906   
4  0.634750  0.711058  0.828655  0.895826  0.972946  4.442658 -0.061682   

      Z_std     Z_min      Z_1%      Z_3%      Z_5%     Z_10%     Z_15%  \
0  0.585710 -1.048372 -1.010391 -0.993666 -0.957112 -0.897970 -0.821275   
1  0.623933 -1.018787 -1.009865 -1.008992 -1.007377 -0.944074 -0.788080   
2  0.515729 -1.016758 -0.988789 -0.857476 -0.733482 -0.457626 -0.252333   
3  0.520138 -1.022549 -0.987087 -0.970566 -0.954552 -0.915447 -0.871919   
4  0.578022 -1.003249 -0.9

In [48]:
'''test_ts_features_concat_df = remove_useless_cols(test_ts_features_concat_df)
print(test_ts_features_concat_df.shape)
test_ts_features_concat_df.head()'''

'test_ts_features_concat_df = remove_useless_cols(test_ts_features_concat_df)\nprint(test_ts_features_concat_df.shape)\ntest_ts_features_concat_df.head()'

In [49]:
train_temp_df['sii'] = train['sii']

In [50]:
train_has_parquet_df = train_temp_df[train_temp_df['has_parquet'] == 1].reset_index(drop=True).drop('has_parquet', axis=1)
print(train_has_parquet_df.shape)
train_has_parquet_df.head()

(996, 130)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00115b9f                    Winter                9                0   
1  001f3379                    Spring               13                1   
2  00f332d1                    Winter               14                0   
3  01085eb3                      Fall               12                0   
4  012cadd8                    Spring                9                0   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0        Fall             71.0          Summer     18.292347             56.0   
1      Winter             50.0          Summer     22.279952             59.5   
2      Spring             68.0          Spring     17.168636             66.5   
3      Winter             58.0            Fall     34.187282             60.5   
4      Winter             60.0            Fall     17.089151             53.2   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             81.6                           NaN                   60.0   
1            112.2                           NaN                   60.0   
2            108.0                           NaN                   60.0   
3            178.0                           NaN                   67.0   
4             68.8                           NaN                   62.0   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                97.0                 117.0                   Summer   
1                73.0                 102.0                      NaN   
2                71.0                 129.0                      NaN   
3                81.0                 119.0                      NaN   
4                88.0                 123.0                     Fall   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          6.0                          9.0   
1                          NaN                          NaN   
2                          NaN                          NaN   
3                          NaN                          NaN   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                        37.0     Summer        18.0              1.0   
1                         NaN     Summer        12.0              0.0   
2                         NaN     Spring        16.0              0.0   
3                         NaN       Fall         8.0              0.0   
4                         NaN       Fall         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         5.0   
1          16.5                2.0         17.9               2.0         6.0   
2          18.4                1.0         20.9               2.0        22.0   
3          12.6                2.0         17.6               2.0         0.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          7.0   
1              0.0         10.0               1.0         11.0   
2              1.0          3.5               0.0          5.5   
3              0.0          4.0               0.0          6.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         7.0              1.0     Summer   
1               1.0         8.0              0.0     Summer   
2               0.0        13.0              1.0     Spring   
3               0.0        11.0              1.0       Fall   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         3.0     

In [51]:
train_nonan_df = train_has_parquet_df[~train_has_parquet_df['sii'].isna()].reset_index(drop=True)
print(train_nonan_df.shape)
train_nonan_df.head()

(996, 130)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00115b9f                    Winter                9                0   
1  001f3379                    Spring               13                1   
2  00f332d1                    Winter               14                0   
3  01085eb3                      Fall               12                0   
4  012cadd8                    Spring                9                0   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0        Fall             71.0          Summer     18.292347             56.0   
1      Winter             50.0          Summer     22.279952             59.5   
2      Spring             68.0          Spring     17.168636             66.5   
3      Winter             58.0            Fall     34.187282             60.5   
4      Winter             60.0            Fall     17.089151             53.2   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             81.6                           NaN                   60.0   
1            112.2                           NaN                   60.0   
2            108.0                           NaN                   60.0   
3            178.0                           NaN                   67.0   
4             68.8                           NaN                   62.0   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                97.0                 117.0                   Summer   
1                73.0                 102.0                      NaN   
2                71.0                 129.0                      NaN   
3                81.0                 119.0                      NaN   
4                88.0                 123.0                     Fall   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          6.0                          9.0   
1                          NaN                          NaN   
2                          NaN                          NaN   
3                          NaN                          NaN   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                        37.0     Summer        18.0              1.0   
1                         NaN     Summer        12.0              0.0   
2                         NaN     Spring        16.0              0.0   
3                         NaN       Fall         8.0              0.0   
4                         NaN       Fall         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         5.0   
1          16.5                2.0         17.9               2.0         6.0   
2          18.4                1.0         20.9               2.0        22.0   
3          12.6                2.0         17.6               2.0         0.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          7.0   
1              0.0         10.0               1.0         11.0   
2              1.0          3.5               0.0          5.5   
3              0.0          4.0               0.0          6.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         7.0              1.0     Summer   
1               1.0         8.0              0.0     Summer   
2               0.0        13.0              1.0     Spring   
3               0.0        11.0              1.0       Fall   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         3.0     

In [52]:
train_nonan_df.shape[1] + train_ts_features_concat_df.shape[1]

27805

In [53]:
train_nonan_df.isna().sum().sum()

16843

In [54]:
train_ts_features_concat_df.isna().sum().sum()

1016675

In [55]:
train_nonan_df.isna().sum().sum() + train_ts_features_concat_df.isna().sum().sum()

1033518

In [56]:
train_merge_df = train_nonan_df.merge(train_ts_features_concat_df, how='inner', on='id')
print(train_merge_df.shape)
train_merge_df.head()

(996, 27804)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00115b9f                    Winter                9                0   
1  001f3379                    Spring               13                1   
2  00f332d1                    Winter               14                0   
3  01085eb3                      Fall               12                0   
4  012cadd8                    Spring                9                0   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0        Fall             71.0          Summer     18.292347             56.0   
1      Winter             50.0          Summer     22.279952             59.5   
2      Spring             68.0          Spring     17.168636             66.5   
3      Winter             58.0            Fall     34.187282             60.5   
4      Winter             60.0            Fall     17.089151             53.2   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             81.6                           NaN                   60.0   
1            112.2                           NaN                   60.0   
2            108.0                           NaN                   60.0   
3            178.0                           NaN                   67.0   
4             68.8                           NaN                   62.0   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                97.0                 117.0                   Summer   
1                73.0                 102.0                      NaN   
2                71.0                 129.0                      NaN   
3                81.0                 119.0                      NaN   
4                88.0                 123.0                     Fall   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          6.0                          9.0   
1                          NaN                          NaN   
2                          NaN                          NaN   
3                          NaN                          NaN   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                        37.0     Summer        18.0              1.0   
1                         NaN     Summer        12.0              0.0   
2                         NaN     Spring        16.0              0.0   
3                         NaN       Fall         8.0              0.0   
4                         NaN       Fall         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         5.0   
1          16.5                2.0         17.9               2.0         6.0   
2          18.4                1.0         20.9               2.0        22.0   
3          12.6                2.0         17.6               2.0         0.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          7.0   
1              0.0         10.0               1.0         11.0   
2              1.0          3.5               0.0          5.5   
3              0.0          4.0               0.0          6.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         7.0              1.0     Summer   
1               1.0         8.0              0.0     Summer   
2               0.0        13.0              1.0     Spring   
3               0.0        11.0              1.0       Fall   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         3.0     

In [57]:
train_merge_df.isna().sum().sum()

1033518

In [58]:
(train_nonan_df['id'] == train_ts_features_concat_df['id']).sum()

996

In [59]:
train_merge_sii = train_merge_df['sii']
train_merge_sii

0      1.0
1      1.0
2      1.0
3      0.0
4      0.0
      ... 
991    0.0
992    0.0
993    0.0
994    1.0
995    0.0
Name: sii, Length: 996, dtype: float64

In [60]:
train_merge_df.drop('sii', axis=1, inplace=True)
print(train_merge_df.shape)
train_merge_df.head()

(996, 27803)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00115b9f                    Winter                9                0   
1  001f3379                    Spring               13                1   
2  00f332d1                    Winter               14                0   
3  01085eb3                      Fall               12                0   
4  012cadd8                    Spring                9                0   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0        Fall             71.0          Summer     18.292347             56.0   
1      Winter             50.0          Summer     22.279952             59.5   
2      Spring             68.0          Spring     17.168636             66.5   
3      Winter             58.0            Fall     34.187282             60.5   
4      Winter             60.0            Fall     17.089151             53.2   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             81.6                           NaN                   60.0   
1            112.2                           NaN                   60.0   
2            108.0                           NaN                   60.0   
3            178.0                           NaN                   67.0   
4             68.8                           NaN                   62.0   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                97.0                 117.0                   Summer   
1                73.0                 102.0                      NaN   
2                71.0                 129.0                      NaN   
3                81.0                 119.0                      NaN   
4                88.0                 123.0                     Fall   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          6.0                          9.0   
1                          NaN                          NaN   
2                          NaN                          NaN   
3                          NaN                          NaN   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                        37.0     Summer        18.0              1.0   
1                         NaN     Summer        12.0              0.0   
2                         NaN     Spring        16.0              0.0   
3                         NaN       Fall         8.0              0.0   
4                         NaN       Fall         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         5.0   
1          16.5                2.0         17.9               2.0         6.0   
2          18.4                1.0         20.9               2.0        22.0   
3          12.6                2.0         17.6               2.0         0.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          7.0   
1              0.0         10.0               1.0         11.0   
2              1.0          3.5               0.0          5.5   
3              0.0          4.0               0.0          6.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         7.0              1.0     Summer   
1               1.0         8.0              0.0     Summer   
2               0.0        13.0              1.0     Spring   
3               0.0        11.0              1.0       Fall   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         3.0     

In [61]:
def remove_pciat_cols(df):
    cols_to_drop = []
    for col in df.columns:
        if 'PCIAT' in col:
            cols_to_drop.append(col)

    df.drop(cols_to_drop, axis=1, inplace=True)
    
    return df

In [62]:
train_merge_df = remove_pciat_cols(train_merge_df)
print(train_merge_df.shape)
train_merge_df.head()

(996, 27803)


id Basic_Demos-Enroll_Season  Basic_Demos-Age  Basic_Demos-Sex  \
0  00115b9f                    Winter                9                0   
1  001f3379                    Spring               13                1   
2  00f332d1                    Winter               14                0   
3  01085eb3                      Fall               12                0   
4  012cadd8                    Spring                9                0   

  CGAS-Season  CGAS-CGAS_Score Physical-Season  Physical-BMI  Physical-Height  \
0        Fall             71.0          Summer     18.292347             56.0   
1      Winter             50.0          Summer     22.279952             59.5   
2      Spring             68.0          Spring     17.168636             66.5   
3      Winter             58.0            Fall     34.187282             60.5   
4      Winter             60.0            Fall     17.089151             53.2   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             81.6                           NaN                   60.0   
1            112.2                           NaN                   60.0   
2            108.0                           NaN                   60.0   
3            178.0                           NaN                   67.0   
4             68.8                           NaN                   62.0   

   Physical-HeartRate  Physical-Systolic_BP Fitness_Endurance-Season  \
0                97.0                 117.0                   Summer   
1                73.0                 102.0                      NaN   
2                71.0                 129.0                      NaN   
3                81.0                 119.0                      NaN   
4                88.0                 123.0                     Fall   

   Fitness_Endurance-Max_Stage  Fitness_Endurance-Time_Mins  \
0                          6.0                          9.0   
1                          NaN                          NaN   
2                          NaN                          NaN   
3                          NaN                          NaN   
4                          NaN                          NaN   

   Fitness_Endurance-Time_Sec FGC-Season  FGC-FGC_CU  FGC-FGC_CU_Zone  \
0                        37.0     Summer        18.0              1.0   
1                         NaN     Summer        12.0              0.0   
2                         NaN     Spring        16.0              0.0   
3                         NaN       Fall         8.0              0.0   
4                         NaN       Fall         NaN              NaN   

   FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  FGC-FGC_GSD_Zone  FGC-FGC_PU  \
0           NaN                NaN          NaN               NaN         5.0   
1          16.5                2.0         17.9               2.0         6.0   
2          18.4                1.0         20.9               2.0        22.0   
3          12.6                2.0         17.6               2.0         0.0   
4           NaN                NaN          NaN               NaN         NaN   

   FGC-FGC_PU_Zone  FGC-FGC_SRL  FGC-FGC_SRL_Zone  FGC-FGC_SRR  \
0              0.0          7.0               0.0          7.0   
1              0.0         10.0               1.0         11.0   
2              1.0          3.5               0.0          5.5   
3              0.0          4.0               0.0          6.0   
4              NaN          NaN               NaN          NaN   

   FGC-FGC_SRR_Zone  FGC-FGC_TL  FGC-FGC_TL_Zone BIA-Season  \
0               0.0         7.0              1.0     Summer   
1               1.0         8.0              0.0     Summer   
2               0.0        13.0              1.0     Spring   
3               0.0        11.0              1.0       Fall   
4               NaN         NaN              NaN        NaN   

   BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  BIA-BIA_BMR  \
0                         3.0     

In [63]:
for col in train_merge_df.columns:
    if 'PCIAT' in col:
        print(col)

In [64]:
cat_cols = []
for i in range(data_dict.shape[0]):
    col = data_dict['Field'][i]
    if col == 'id':
        continue
    if (data_dict['Type'][i] == 'str') | ('categori' in data_dict['Type'][i]):
        cat_cols.append(col)

In [65]:
ordinal_variables = ['FGC-FGC_CU_Zone', 'FGC-FGC_CU_Zone', 'FGC-FGC_GSND_Zone', 'FGC-FGC_GSD_Zone', 'FGC-FGC_PU_Zone',
                     'FGC-FGC_SRL_Zone', 'FGC-FGC_SRR_Zone', 'FGC-FGC_TL_Zone', 'BIA-BIA_Activity_Level_num', 'BIA-BIA_Frame_num',
                     'PreInt_EduHx-computerinternet_hoursday']

ordinal_variables += [col for col in cat_cols if (('PCIAT' in col)&('Season' not in col))]
print(len(ordinal_variables))
ordinal_variables

31


['FGC-FGC_CU_Zone',
 'FGC-FGC_CU_Zone',
 'FGC-FGC_GSND_Zone',
 'FGC-FGC_GSD_Zone',
 'FGC-FGC_PU_Zone',
 'FGC-FGC_SRL_Zone',
 'FGC-FGC_SRR_Zone',
 'FGC-FGC_TL_Zone',
 'BIA-BIA_Activity_Level_num',
 'BIA-BIA_Frame_num',
 'PreInt_EduHx-computerinternet_hoursday',
 'PCIAT-PCIAT_01',
 'PCIAT-PCIAT_02',
 'PCIAT-PCIAT_03',
 'PCIAT-PCIAT_04',
 'PCIAT-PCIAT_05',
 'PCIAT-PCIAT_06',
 'PCIAT-PCIAT_07',
 'PCIAT-PCIAT_08',
 'PCIAT-PCIAT_09',
 'PCIAT-PCIAT_10',
 'PCIAT-PCIAT_11',
 'PCIAT-PCIAT_12',
 'PCIAT-PCIAT_13',
 'PCIAT-PCIAT_14',
 'PCIAT-PCIAT_15',
 'PCIAT-PCIAT_16',
 'PCIAT-PCIAT_17',
 'PCIAT-PCIAT_18',
 'PCIAT-PCIAT_19',
 'PCIAT-PCIAT_20']

In [66]:
cat_cols = list(set(cat_cols) - set(ordinal_variables))
cat_cols = [col for col in cat_cols if 'PCIAT' not in col]
print(len(cat_cols))
cat_cols

11


['PreInt_EduHx-Season',
 'PAQ_A-Season',
 'Basic_Demos-Enroll_Season',
 'PAQ_C-Season',
 'Basic_Demos-Sex',
 'Physical-Season',
 'FGC-Season',
 'Fitness_Endurance-Season',
 'BIA-Season',
 'CGAS-Season',
 'SDS-Season']

In [67]:
for col in cat_cols:
    if col in train_merge_df.columns.tolist():
        print(col)

PreInt_EduHx-Season
PAQ_A-Season
Basic_Demos-Enroll_Season
PAQ_C-Season
Basic_Demos-Sex
Physical-Season
FGC-Season
Fitness_Endurance-Season
BIA-Season
CGAS-Season
SDS-Season


In [68]:
train_one_hot_df = train_merge_df.copy()

In [69]:
def one_hot_cat_cols(df):
    for col in tqdm(cat_cols):
        df[col] = df[col].fillna('Missing').apply(str)
        unique_list = sorted(df[col].unique().tolist())

        for v in unique_list:
            new_col_name = col + '_' + v
            df[new_col_name] = (df[col] == v).astype(int)
    
    df = df.drop(cat_cols, axis=1)

    return df

In [70]:
train_one_hot_df = one_hot_cat_cols(train_one_hot_df)
print(train_one_hot_df.shape)
train_one_hot_df.head()

100%|█████████████████████████████████████████████████████████████████████████████████| 11/11 [00:00<00:00, 135.67it/s]


(996, 27843)


id  Basic_Demos-Age  CGAS-CGAS_Score  Physical-BMI  Physical-Height  \
0  00115b9f                9             71.0     18.292347             56.0   
1  001f3379               13             50.0     22.279952             59.5   
2  00f332d1               14             68.0     17.168636             66.5   
3  01085eb3               12             58.0     34.187282             60.5   
4  012cadd8                9             60.0     17.089151             53.2   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             81.6                           NaN                   60.0   
1            112.2                           NaN                   60.0   
2            108.0                           NaN                   60.0   
3            178.0                           NaN                   67.0   
4             68.8                           NaN                   62.0   

   Physical-HeartRate  Physical-Systolic_BP  Fitness_Endurance-Max_Stage  \
0                97.0                 117.0                          6.0   
1                73.0                 102.0                          NaN   
2                71.0                 129.0                          NaN   
3                81.0                 119.0                          NaN   
4                88.0                 123.0                          NaN   

   Fitness_Endurance-Time_Mins  Fitness_Endurance-Time_Sec  FGC-FGC_CU  \
0                          9.0                        37.0        18.0   
1                          NaN                         NaN        12.0   
2                          NaN                         NaN        16.0   
3                          NaN                         NaN         8.0   
4                          NaN                         NaN         NaN   

   FGC-FGC_CU_Zone  FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  \
0              1.0           NaN                NaN          NaN   
1              0.0          16.5                2.0         17.9   
2              0.0          18.4                1.0         20.9   
3              0.0          12.6                2.0         17.6   
4              NaN           NaN                NaN          NaN   

   FGC-FGC_GSD_Zone  FGC-FGC_PU  FGC-FGC_PU_Zone  FGC-FGC_SRL  \
0               NaN         5.0              0.0          7.0   
1               2.0         6.0              0.0         10.0   
2               2.0        22.0              1.0          3.5   
3               2.0         0.0              0.0          4.0   
4               NaN         NaN              NaN          NaN   

   FGC-FGC_SRL_Zone  FGC-FGC_SRR  FGC-FGC_SRR_Zone  FGC-FGC_TL  \
0               0.0          7.0               0.0         7.0   
1               1.0         11.0               1.0         8.0   
2               0.0          5.5               0.0        13.0   
3               0.0          6.0               0.0        11.0   
4               NaN          NaN               NaN         NaN   

   FGC-FGC_TL_Zone  BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  \
0              1.0                         3.0      3.84191      18.2943   
1              0.0                         2.0      4.33036      30.1865   
2              1.0                         4.0      5.93056      17.1705   
3              1.0                         1.0      5.15068      34.1910   
4              NaN                         NaN          NaN          NaN   

   BIA-BIA_BMR  BIA-BIA_DEE  BIA-BIA_ECW  BIA-BIA_FFM  BIA-BIA_FFMI  \
0      1131.43      1923.44      15.5925      62.7757       14.0740   
1      1330.97      1996.45      30.2124      84.0285       16.6877   
2      1414.24      2969.90      27.2818      92.8980       14.7695   
3      1551.20      2016.56      33.4786     107.4860       20.6463   
4          NaN          NaN          NaN          NaN           NaN   

   BIA-BIA_FMI  BIA-BIA_Fat  BIA-BIA_Frame_num  BIA-BIA_ICW  BIA-BIA_LDM  \
0      4.22033    

In [71]:
# https://www.kaggle.com/code/ichigoe/lb0-494-with-tabnet
def feature_engineering(df):
    df['BMI_Age'] = df['Physical-BMI'] * df['Basic_Demos-Age']
    df['Internet_Hours_Age'] = df['PreInt_EduHx-computerinternet_hoursday'] * df['Basic_Demos-Age']
    df['BMI_Internet_Hours'] = df['Physical-BMI'] * df['PreInt_EduHx-computerinternet_hoursday']
    df['BFP_BMI'] = df['BIA-BIA_Fat'] / df['BIA-BIA_BMI']
    df['FFMI_BFP'] = df['BIA-BIA_FFMI'] / df['BIA-BIA_Fat']
    df['FMI_BFP'] = df['BIA-BIA_FMI'] / df['BIA-BIA_Fat']
    df['LST_TBW'] = df['BIA-BIA_LST'] / df['BIA-BIA_TBW']
    df['BFP_BMR'] = df['BIA-BIA_Fat'] * df['BIA-BIA_BMR']
    df['BFP_DEE'] = df['BIA-BIA_Fat'] * df['BIA-BIA_DEE']
    df['BMR_Weight'] = df['BIA-BIA_BMR'] / df['Physical-Weight']
    df['DEE_Weight'] = df['BIA-BIA_DEE'] / df['Physical-Weight']
    df['SMM_Height'] = df['BIA-BIA_SMM'] / df['Physical-Height']
    df['Muscle_to_Fat'] = df['BIA-BIA_SMM'] / df['BIA-BIA_FMI']
    df['Hydration_Status'] = df['BIA-BIA_TBW'] / df['Physical-Weight']
    df['ICW_TBW'] = df['BIA-BIA_ICW'] / df['BIA-BIA_TBW']
    
    return df

In [72]:
train_one_hot_df = feature_engineering(train_one_hot_df)
print(train_one_hot_df.shape)
train_one_hot_df.head()

(996, 27858)


id  Basic_Demos-Age  CGAS-CGAS_Score  Physical-BMI  Physical-Height  \
0  00115b9f                9             71.0     18.292347             56.0   
1  001f3379               13             50.0     22.279952             59.5   
2  00f332d1               14             68.0     17.168636             66.5   
3  01085eb3               12             58.0     34.187282             60.5   
4  012cadd8                9             60.0     17.089151             53.2   

   Physical-Weight  Physical-Waist_Circumference  Physical-Diastolic_BP  \
0             81.6                           NaN                   60.0   
1            112.2                           NaN                   60.0   
2            108.0                           NaN                   60.0   
3            178.0                           NaN                   67.0   
4             68.8                           NaN                   62.0   

   Physical-HeartRate  Physical-Systolic_BP  Fitness_Endurance-Max_Stage  \
0                97.0                 117.0                          6.0   
1                73.0                 102.0                          NaN   
2                71.0                 129.0                          NaN   
3                81.0                 119.0                          NaN   
4                88.0                 123.0                          NaN   

   Fitness_Endurance-Time_Mins  Fitness_Endurance-Time_Sec  FGC-FGC_CU  \
0                          9.0                        37.0        18.0   
1                          NaN                         NaN        12.0   
2                          NaN                         NaN        16.0   
3                          NaN                         NaN         8.0   
4                          NaN                         NaN         NaN   

   FGC-FGC_CU_Zone  FGC-FGC_GSND  FGC-FGC_GSND_Zone  FGC-FGC_GSD  \
0              1.0           NaN                NaN          NaN   
1              0.0          16.5                2.0         17.9   
2              0.0          18.4                1.0         20.9   
3              0.0          12.6                2.0         17.6   
4              NaN           NaN                NaN          NaN   

   FGC-FGC_GSD_Zone  FGC-FGC_PU  FGC-FGC_PU_Zone  FGC-FGC_SRL  \
0               NaN         5.0              0.0          7.0   
1               2.0         6.0              0.0         10.0   
2               2.0        22.0              1.0          3.5   
3               2.0         0.0              0.0          4.0   
4               NaN         NaN              NaN          NaN   

   FGC-FGC_SRL_Zone  FGC-FGC_SRR  FGC-FGC_SRR_Zone  FGC-FGC_TL  \
0               0.0          7.0               0.0         7.0   
1               1.0         11.0               1.0         8.0   
2               0.0          5.5               0.0        13.0   
3               0.0          6.0               0.0        11.0   
4               NaN          NaN               NaN         NaN   

   FGC-FGC_TL_Zone  BIA-BIA_Activity_Level_num  BIA-BIA_BMC  BIA-BIA_BMI  \
0              1.0                         3.0      3.84191      18.2943   
1              0.0                         2.0      4.33036      30.1865   
2              1.0                         4.0      5.93056      17.1705   
3              1.0                         1.0      5.15068      34.1910   
4              NaN                         NaN          NaN          NaN   

   BIA-BIA_BMR  BIA-BIA_DEE  BIA-BIA_ECW  BIA-BIA_FFM  BIA-BIA_FFMI  \
0      1131.43      1923.44      15.5925      62.7757       14.0740   
1      1330.97      1996.45      30.2124      84.0285       16.6877   
2      1414.24      2969.90      27.2818      92.8980       14.7695   
3      1551.20      2016.56      33.4786     107.4860       20.6463   
4          NaN          NaN          NaN          NaN           NaN   

   BIA-BIA_FMI  BIA-BIA_Fat  BIA-BIA_Frame_num  BIA-BIA_ICW  BIA-BIA_LDM  \
0      4.22033    

In [73]:
no_id_cols = [col for col in train_one_hot_df.columns if col != 'id']
print(len(no_id_cols))
no_id_cols[:5]

27857


['Basic_Demos-Age',
 'CGAS-CGAS_Score',
 'Physical-BMI',
 'Physical-Height',
 'Physical-Weight']

In [74]:
if np.any(np.isinf(train_one_hot_df[no_id_cols])):
    print('inf in data')
    train_one_hot_df[no_id_cols] = train_one_hot_df[no_id_cols].replace([np.inf, -np.inf], np.nan)

inf in data


In [75]:
imputer = KNNImputer(n_neighbors=5)
train_one_hot_df[no_id_cols] = imputer.fit_transform(train_one_hot_df[no_id_cols])

In [76]:
train_one_hot_df.isna().sum().sum()

0

In [77]:
train_one_hot_df['sii'] = train_merge_sii

In [78]:
train_final_df = train_one_hot_df.copy()

In [79]:
# https://www.kaggle.com/code/ichigoe/lb0-494-with-tabnet
def quadratic_weighted_kappa(y_true, y_pred):
    return cohen_kappa_score(y_true, y_pred, weights='quadratic')

def threshold_Rounder(oof_non_rounded, thresholds):
    return np.where(oof_non_rounded < thresholds[0], 0,
                    np.where(oof_non_rounded < thresholds[1], 1,
                             np.where(oof_non_rounded < thresholds[2], 2, 3)))

def evaluate_predictions(thresholds, y_true, oof_non_rounded):
    rounded_p = threshold_Rounder(oof_non_rounded, thresholds)
    return -quadratic_weighted_kappa(y_true, rounded_p)

In [128]:
def custom_qwk_metric(y_true, y_pred):
    """
    Custom QWK metric for CatBoost.
    CatBoost passes logits as predictions, so you need to convert them to class probabilities or class indices.
    """
    y_pred_classes = np.argmax(y_pred, axis=1)  # Convert logits to class indices
    kappa = quadratic_weighted_kappa(y_true, y_pred_classes)
    return kappa

# Wrap the function for CatBoost
def qwk_wrapper(preds, train_data):
    labels = train_data.get_label()
    kappa = custom_qwk_metric(labels, preds)
    return "qwk", kappa, True  # Name, value, higher_is_better

In [229]:
# https://www.kaggle.com/code/ichigoe/lb0-494-with-tabnet
def TrainML(model_class, train_data):#, test_data):
    X = train_data.drop(['id', 'sii'], axis=1)
    y = train_data['sii']

    SKF = StratifiedKFold(n_splits=n_splits, shuffle=True)#, random_state=SEED)
    
    train_S = []
    test_S = []
    
    oof_non_rounded = np.zeros(len(y), dtype=float) 
    oof_rounded = np.zeros(len(y), dtype=int) 
    #test_preds = np.zeros((len(test_data), n_splits))

    models_list = []

    #for fold, (train_idx, test_idx) in enumerate(tqdm(SKF.split(X, y), desc="Training Folds", total=n_splits)):
    for fold, (train_idx, test_idx) in enumerate(SKF.split(X, y)):
        X_train, X_val = X.iloc[train_idx], X.iloc[test_idx]
        y_train, y_val = y.iloc[train_idx], y.iloc[test_idx]

        model = clone(model_class)
        model.fit(X_train, y_train, eval_set=(X_val, y_val))

        y_train_pred = model.predict(X_train)
        y_val_pred = model.predict(X_val)

        oof_non_rounded[test_idx] = y_val_pred
        y_val_pred_rounded = y_val_pred.round(0).astype(int)
        oof_rounded[test_idx] = y_val_pred_rounded

        train_kappa = quadratic_weighted_kappa(y_train, y_train_pred.round(0).astype(int))
        val_kappa = quadratic_weighted_kappa(y_val, y_val_pred_rounded)

        train_S.append(train_kappa)
        test_S.append(val_kappa)
        
        #test_preds[:, fold] = model.predict(test_data)
        
        print(f"Fold {fold+1} - Train QWK: {train_kappa:.4f}, Validation QWK: {val_kappa:.4f}")
        #clear_output(wait=True)

        models_list.append(model)

    print(f"Mean Train QWK --> {np.mean(train_S):.4f}")
    print(f"Mean Validation QWK ---> {np.mean(test_S):.4f}")

    KappaOPtimizer = minimize(evaluate_predictions,
                              x0=[0.5, 1.5, 2.5], args=(y, oof_non_rounded), 
                              method='Nelder-Mead')
    assert KappaOPtimizer.success, "Optimization did not converge."
    
    oof_tuned = threshold_Rounder(oof_non_rounded, KappaOPtimizer.x)
    tKappa = quadratic_weighted_kappa(y, oof_tuned)

    print(f"----> || Optimized QWK SCORE :: {Fore.CYAN}{Style.BRIGHT} {tKappa:.3f}{Style.RESET_ALL}")

    #tpm = test_preds.mean(axis=1)
    #tpTuned = threshold_Rounder(tpm, KappaOPtimizer.x)
    
    '''submission = pd.DataFrame({
        'id': sample['id'],
        'sii': tpTuned
    })'''

    return models_list #submission

In [230]:
#Light = LGBMRegressor(**Params7, random_state=SEED, verbose=1, n_estimators=200)

In [231]:
Params7 = {
    #'learning_rate': 0.03884249148676395,
    #'max_depth': 12,
    #'num_leaves': 413,
    #'min_data_in_leaf': 14,
    #'feature_fraction': 0.7987976913702801,
    #'bagging_fraction': 0.7602261703576205,
    #'bagging_freq': 2,
    #'lambda_l1': 4.735462555910575,
    #'lambda_l2': 4.735028557007343e-06
} # CV : 0.4094 | LB : 0.471

In [232]:
Light = LGBMRegressor(n_estimators=200)

In [233]:
CatBoost_Params = {
    'learning_rate': 0.003,
    'depth': 6,
    'iterations': 200,
    'random_seed': SEED,
    'verbose': 1,
    'l2_leaf_reg': 10,  # Increase this value
    'task_type': 'GPU'
}

In [234]:
CatBoost_Model = CatBoostRegressor(
    **CatBoost_Params,
    use_best_model=True
    #custom_metric=[quadratic_weighted_kappa]#,  # Use custom QWK as an additional metric
    #eval_metric=qwk_wrapper       # Optionally use it as the primary evaluation metric
)

In [235]:
RandomForestRegressor(random_state=SEED)

RandomForestRegressor(random_state=42)

In [ ]:
CatBoost_Params = {
    'learning_rate': 0.001,
    'depth': 10,
    'iterations': 1000,
    'random_seed': SEED,
    'verbose': 1,
    'l2_leaf_reg': 10,  # Increase this value
    'task_type': 'GPU'
}

CatBoost_Model = CatBoostRegressor(
    **CatBoost_Params,
    use_best_model=True
    #custom_metric=[quadratic_weighted_kappa]#,  # Use custom QWK as an additional metric
    #eval_metric=qwk_wrapper       # Optionally use it as the primary evaluation metric
)

catboost_models_list = TrainML(CatBoost_Model, train_final_df)#, test_final)

In [236]:
#catboost_models_list = TrainML(CatBoost_Model, train_final_df)#, test_final)

0:	learn: 0.7606309	test: 0.7637159	best: 0.7637159 (0)	total: 334ms	remaining: 1m 6s
1:	learn: 0.7602468	test: 0.7635387	best: 0.7635387 (1)	total: 481ms	remaining: 47.6s
2:	learn: 0.7597988	test: 0.7634090	best: 0.7634090 (2)	total: 630ms	remaining: 41.4s
3:	learn: 0.7593308	test: 0.7631907	best: 0.7631907 (3)	total: 778ms	remaining: 38.1s
4:	learn: 0.7588502	test: 0.7630285	best: 0.7630285 (4)	total: 926ms	remaining: 36.1s
5:	learn: 0.7584090	test: 0.7628309	best: 0.7628309 (5)	total: 1.07s	remaining: 34.6s
6:	learn: 0.7579836	test: 0.7626690	best: 0.7626690 (6)	total: 1.22s	remaining: 33.7s
7:	learn: 0.7575464	test: 0.7624575	best: 0.7624575 (7)	total: 1.39s	remaining: 33.5s
8:	learn: 0.7570251	test: 0.7621970	best: 0.7621970 (8)	total: 1.54s	remaining: 32.8s
9:	learn: 0.7565731	test: 0.7619312	best: 0.7619312 (9)	total: 1.69s	remaining: 32.1s
10:	learn: 0.7560747	test: 0.7617244	best: 0.7617244 (10)	total: 1.84s	remaining: 31.7s
11:	learn: 0.7556347	test: 0.7616319	best: 0.7616319

In [237]:
len(catboost_models_list)

5

In [240]:
def feature_importance(model, X):
    feature_importance = model.get_feature_importance(type='FeatureImportance')
    feature_names = X.columns
    
    # Create a DataFrame for better visualization
    importance_df = pd.DataFrame({
        'Feature': feature_names,
        'Importance': feature_importance
    }).sort_values(by='Importance', ascending=False)
    
    return importance_df

In [241]:
catboost_importance_df = feature_importance(catboost_models_list[0], train_final_df.drop(['id', 'sii'], axis=1))
print(catboost_importance_df.shape)
catboost_importance_df.head()

(27857, 2)


Feature  Importance
27843                      Internet_Hours_Age   12.602312
27842                                 BMI_Age    9.356843
4                             Physical-Weight    5.591795
46     PreInt_EduHx-computerinternet_hoursday    2.947192
17666   enmo_time_of_day_15_min_window_73_75%    2.157146

In [242]:
catboost_importance_df

Feature  Importance
27843                      Internet_Hours_Age   12.602312
27842                                 BMI_Age    9.356843
4                             Physical-Weight    5.591795
46     PreInt_EduHx-computerinternet_hoursday    2.947192
17666   enmo_time_of_day_15_min_window_73_75%    2.157146
...                                       ...         ...
9418       X_time_of_day_15_min_window_86_85%    0.000000
9417       X_time_of_day_15_min_window_86_80%    0.000000
9416       X_time_of_day_15_min_window_86_75%    0.000000
9415       X_time_of_day_15_min_window_86_70%    0.000000
27856                                 ICW_TBW    0.000000

[27857 rows x 2 columns]

In [245]:
unimportant_features_df = catboost_importance_df[catboost_importance_df['Importance'] == 0]

In [247]:
unimportant_features = unimportant_features_df['Feature'].tolist()
print(len(unimportant_features))
unimportant_features[:5]

27096


['enmo_time_of_day_15_min_window_79_80%',
 'anglez_time_of_day_15_min_window_13_70%',
 'anglez_time_of_day_15_min_window_14_10%',
 'enmo_time_of_day_15_min_window_78_10%',
 'anglez_time_of_day_15_min_window_13_65%']

In [248]:
selected_train_df = train_final_df.drop(unimportant_features, axis=1)
print(selected_train_df.shape)
selected_train_df.head()

(996, 763)


id  Basic_Demos-Age  Physical-Height  Physical-Weight  FGC-FGC_PU  \
0  00115b9f              9.0             56.0             81.6         5.0   
1  001f3379             13.0             59.5            112.2         6.0   
2  00f332d1             14.0             66.5            108.0        22.0   
3  01085eb3             12.0             60.5            178.0         0.0   
4  012cadd8              9.0             53.2             68.8         4.6   

   FGC-FGC_TL_Zone  BIA-BIA_BMC  BIA-BIA_BMR  BIA-BIA_FFM  BIA-BIA_FFMI  \
0              1.0      3.84191    1131.4300     62.77570       14.0740   
1              0.0      4.33036    1330.9700     84.02850       16.6877   
2              1.0      5.93056    1414.2400     92.89800       14.7695   
3              1.0      5.15068    1551.2000    107.48600       20.6463   
4              1.0      3.65138    1128.7328     62.48774       14.5418   

   BIA-BIA_ICW  BIA-BIA_LDM  SDS-SDS_Total_Raw  SDS-SDS_Total_T  \
0     30.40410     16.77900               31.0             45.0   
1     32.91410     20.90200               40.0             56.0   
2     41.40040     24.21580               30.0             43.0   
3     47.22380     26.78340               53.0             73.0   
4     29.57456     16.84324               27.0             40.0   

   PreInt_EduHx-computerinternet_hoursday     X_15%     Y_max  light_75%  \
0                                     0.0 -0.811414  1.666354  15.000000   
1                                     0.0 -0.744080  1.946303  10.533334   
2                                     2.0 -0.376297  1.016429  18.161591   
3                                     0.0 -0.890299  1.011419  18.274206   
4                                     0.0 -0.722694  4.442658  19.320485   

   X_weekday_2_entropy  X_weekday_3_min  X_weekday_3_max  X_weekday_4_35%  \
0             9.026580        -0.973490         0.985729        -0.451854   
1            27.247614        -1.015088         1.006678         0.044092   
2            15.034807        -1.553576         1.104076         0.110742   
3            12.152884        -2.284304         0.996359        -0.683567   
4            11.612482        -0.988268         0.967703         0.012306   

   X_weekday_4_50%  X_weekday_4_70%  X_weekday_7_75%  X_weekday_7_90%  \
0        -0.207005         0.040870         0.090599         0.638867   
1         0.338592         0.695451         0.552708         0.734725   
2         0.301320         0.600236         0.717873         0.909538   
3        -0.517692        -0.163174        -0.004704         0.533553   
4         0.376306         0.623529         0.829352         0.948852   

   Y_weekday_2_75%  Y_weekday_5_count  Y_weekday_5_3%  Y_weekday_6_5%  \
0         0.652526            10223.0       -0.927320       -0.696904   
1         0.193994            17467.0       -0.743804       -0.676679   
2         0.414495            51840.0       -0.956012       -0.789148   
3         0.220756            51840.0       -0.908165       -0.770310   
4         0.256043            17280.0       -0.931767       -0.881196   

   Z_weekday_1_70%  Z_weekday_2_3%  Z_weekday_4_30%  Z_weekday_4_50%  \
0         0.030208       -0.965397        -0.418682        -0.034375   
1         0.589082       -1.010596        -0.536273        -0.027865   
2         0.697727       -0.873446         0.158338         0.430185   
3         0.009463       -0.969265        -0.682861        -0.372104   
4         0.366585       -0.973023        -0.256970        -0.010006   

   Z_weekday_4_60%  Z_weekday_5_std  Z_weekday_6_97%  Z_weekday_7_45%  \
0         0.109281         0.581047         0.947157        -0.405566   
1         0.074222         0.636366         0.960648        -0.039792   
2         0.538868         0.444914         1.002965         0.292192   
3        -0.200923         0.533165         0.755191        -0.475323   
4         0.087781         0.553874         0.956632        -0.177210   

   enmo_weekday_

In [249]:
catboost_models_list = TrainML(CatBoost_Model, selected_train_df)#, test_final)

0:	learn: 0.7606225	test: 0.7636853	best: 0.7636853 (0)	total: 8.59ms	remaining: 1.71s
1:	learn: 0.7601298	test: 0.7634116	best: 0.7634116 (1)	total: 16.3ms	remaining: 1.61s
2:	learn: 0.7597038	test: 0.7631477	best: 0.7631477 (2)	total: 25.4ms	remaining: 1.67s
3:	learn: 0.7592289	test: 0.7629074	best: 0.7629074 (3)	total: 34.6ms	remaining: 1.69s
4:	learn: 0.7587713	test: 0.7626394	best: 0.7626394 (4)	total: 41.9ms	remaining: 1.63s
5:	learn: 0.7583690	test: 0.7624350	best: 0.7624350 (5)	total: 49.4ms	remaining: 1.6s
6:	learn: 0.7579154	test: 0.7622282	best: 0.7622282 (6)	total: 56.9ms	remaining: 1.57s
7:	learn: 0.7574699	test: 0.7619703	best: 0.7619703 (7)	total: 64.4ms	remaining: 1.54s
8:	learn: 0.7570074	test: 0.7617966	best: 0.7617966 (8)	total: 72ms	remaining: 1.53s
9:	learn: 0.7565824	test: 0.7615693	best: 0.7615693 (9)	total: 79.6ms	remaining: 1.51s
10:	learn: 0.7561397	test: 0.7612584	best: 0.7612584 (10)	total: 88.6ms	remaining: 1.52s
11:	learn: 0.7556532	test: 0.7610097	best: 0

In [251]:
catboost_importance_df = feature_importance(catboost_models_list[0], selected_train_df.drop(['id', 'sii'], axis=1))
print(catboost_importance_df.shape)
catboost_importance_df

(761, 2)


Feature  Importance
757                     Internet_Hours_Age   16.876700
756                                BMI_Age    8.622090
758                     BMI_Internet_Hours    3.197219
0                          Basic_Demos-Age    3.155194
511  enmo_time_of_day_15_min_window_62_70%    3.099592
..                                     ...         ...
152   anglez_time_of_day_hour_window_6_50%    0.000000
157  anglez_time_of_day_hour_window_16_80%    0.000000
429      Z_time_of_day_15_min_window_93_3%    0.000000
427     Z_time_of_day_15_min_window_90_65%    0.000000
380     Z_time_of_day_15_min_window_38_70%    0.000000

[761 rows x 2 columns]

In [252]:
unimportant_features_df = catboost_importance_df[catboost_importance_df['Importance'] == 0]
unimportant_features = unimportant_features_df['Feature'].tolist()
print(len(unimportant_features))
unimportant_features[:5]

366


['light_time_of_day_15_min_window_17_min',
 'anglez_time_of_day_15_min_window_34_30%',
 'X_time_of_day_hour_window_7_15%',
 'battery_use_since_wear_time_of_day_15_min_window_70_80%',
 'anglez_time_of_day_15_min_window_32_99%']

In [253]:
selected_train_df = selected_train_df.drop(unimportant_features, axis=1)
print(selected_train_df.shape)
selected_train_df.head()

(996, 397)


id  Basic_Demos-Age  Physical-Height  Physical-Weight  BIA-BIA_FFM  \
0  00115b9f              9.0             56.0             81.6     62.77570   
1  001f3379             13.0             59.5            112.2     84.02850   
2  00f332d1             14.0             66.5            108.0     92.89800   
3  01085eb3             12.0             60.5            178.0    107.48600   
4  012cadd8              9.0             53.2             68.8     62.48774   

   BIA-BIA_FFMI  BIA-BIA_ICW  BIA-BIA_LDM  SDS-SDS_Total_Raw  SDS-SDS_Total_T  \
0       14.0740     30.40410     16.77900               31.0             45.0   
1       16.6877     32.91410     20.90200               40.0             56.0   
2       14.7695     41.40040     24.21580               30.0             43.0   
3       20.6463     47.22380     26.78340               53.0             73.0   
4       14.5418     29.57456     16.84324               27.0             40.0   

   PreInt_EduHx-computerinternet_hoursday  X_weekday_2_entropy  \
0                                     0.0             9.026580   
1                                     0.0            27.247614   
2                                     2.0            15.034807   
3                                     0.0            12.152884   
4                                     0.0            11.612482   

   X_weekday_3_min  X_weekday_4_35%  X_weekday_7_75%  X_weekday_7_90%  \
0        -0.973490        -0.451854         0.090599         0.638867   
1        -1.015088         0.044092         0.552708         0.734725   
2        -1.553576         0.110742         0.717873         0.909538   
3        -2.284304        -0.683567        -0.004704         0.533553   
4        -0.988268         0.012306         0.829352         0.948852   

   Y_weekday_2_75%  Z_weekday_1_70%  Z_weekday_2_3%  Z_weekday_5_std  \
0         0.652526         0.030208       -0.965397         0.581047   
1         0.193994         0.589082       -1.010596         0.636366   
2         0.414495         0.697727       -0.873446         0.444914   
3         0.220756         0.009463       -0.969265         0.533165   
4         0.256043         0.366585       -0.973023         0.553874   

   Z_weekday_6_97%  enmo_weekday_2_55%  enmo_weekday_4_20%  \
0         0.947157            0.026504            0.006422   
1         0.960648            0.010453            0.000623   
2         1.002965            0.012948            0.000078   
3         0.755191            0.009927            0.000471   
4         0.956632            0.013931            0.005021   

   anglez_weekday_6_1%  anglez_weekday_6_max  light_weekday_1_10%  \
0           -87.498731             85.119347             1.941022   
1           -88.470515             89.331543             0.744055   
2           -88.602883             88.671829             1.312926   
3           -82.111312             87.303482             1.364101   
4           -87.135750             87.101311             1.995188   

   light_weekday_3_25%  light_weekday_3_60%  light_weekday_5_40%  \
0             3.691755             7.477767             6.748261   
1             1.121339             2.490197             7.652195   
2             1.663496             7.000000             5.989103   
3             2.543231            11.139584             4.537135   
4             5.000000             5.000000             2.163832   

   light_weekday_6_70%  light_weekday_7_70%  \
0             7.500000            13.000000   
1             9.282051             5.310170   
2            95.829414            18.898438   
3             6.329125            17.769334   
4             7.855823            17.909689   

   battery_use_since_wear_weekday_5_3%  battery_use_since_wear_weekday_7_min  \
0                            24.000000                                  54.0   
1                           120.583252                                 190.0   
2                           127.000000                    

In [254]:
catboost_models_list = TrainML(CatBoost_Model, selected_train_df)#, test_final)

0:	learn: 0.7606616	test: 0.7638004	best: 0.7638004 (0)	total: 6.84ms	remaining: 1.36s
1:	learn: 0.7602063	test: 0.7635676	best: 0.7635676 (1)	total: 12.4ms	remaining: 1.23s
2:	learn: 0.7597529	test: 0.7633536	best: 0.7633536 (2)	total: 17.9ms	remaining: 1.18s
3:	learn: 0.7593021	test: 0.7630844	best: 0.7630844 (3)	total: 23.6ms	remaining: 1.16s
4:	learn: 0.7588428	test: 0.7628678	best: 0.7628678 (4)	total: 29.1ms	remaining: 1.14s
5:	learn: 0.7584427	test: 0.7626272	best: 0.7626272 (5)	total: 34.7ms	remaining: 1.12s
6:	learn: 0.7579830	test: 0.7623197	best: 0.7623197 (6)	total: 40.3ms	remaining: 1.11s
7:	learn: 0.7575317	test: 0.7621252	best: 0.7621252 (7)	total: 45.9ms	remaining: 1.1s
8:	learn: 0.7571419	test: 0.7619302	best: 0.7619302 (8)	total: 51.4ms	remaining: 1.09s
9:	learn: 0.7567180	test: 0.7616622	best: 0.7616622 (9)	total: 57ms	remaining: 1.08s
10:	learn: 0.7563063	test: 0.7614027	best: 0.7614027 (10)	total: 62.5ms	remaining: 1.07s
11:	learn: 0.7558986	test: 0.7612148	best: 0

In [255]:
catboost_importance_df = feature_importance(catboost_models_list[0], selected_train_df.drop(['id', 'sii'], axis=1))
print(catboost_importance_df.shape)
catboost_importance_df

(395, 2)


Feature  Importance
391                                       Internet_Hours_Age   21.943355
390                                                  BMI_Age    5.132202
8                                            SDS-SDS_Total_T    3.837760
277                    enmo_time_of_day_15_min_window_73_75%    3.182958
392                                       BMI_Internet_Hours    3.140921
9                     PreInt_EduHx-computerinternet_hoursday    3.009560
7                                          SDS-SDS_Total_Raw    2.895016
278                    enmo_time_of_day_15_min_window_73_80%    2.290443
2                                            Physical-Weight    1.843269
70                       enmo_time_of_day_hour_window_18_80%    1.734516
276                    enmo_time_of_day_15_min_window_73_70%    1.601769
260                    enmo_time_of_day_15_min_window_62_55%    1.443704
238                    enmo_time_of_day_15_min_window_40_75%    1.039120
239                    enmo_time_of_day_15_min_window_41_65%    1.024851
1                                            Physical-Height    0.984099
250                    enmo_time_of_day_15_min_window_58_60%    0.944914
18                                           Z_weekday_5_std    0.914709
69                       enmo_time_of_day_hour_window_18_75%    0.894460
333                  anglez_time_of_day_15_min_window_95_65%    0.830455
389                                        Basic_Demos-Sex_1    0.823767
0                                            Basic_Demos-Age    0.786489
237                    enmo_time_of_day_15_min_window_40_70%    0.678371
332                  anglez_time_of_day_15_min_window_95_50%    0.660286
275                   enmo_time_of_day_15_min_window_73_mean    0.654118
388                                      PAQ_C-Season_Winter    0.651956
252                    enmo_time_of_day_15_min_window_58_75%    0.650122
357                  light_time_of_day_15_min_window_63_mean    0.594505
120                       X_time_of_day_15_min_window_73_20%    0.584659
259                    enmo_time_of_day_15_min_window_62_40%    0.565007
37                          X_time_of_day_hour_window_18_20%    0.545650
341                   light_time_of_day_15_min_window_39_max    0.514627
245                   enmo_time_of_day_15_min_window_53_mean    0.495681
47                          Y_time_of_day_hour_window_17_50%    0.478817
196                       Z_time_of_day_15_min_window_49_97%    0.447772
140                       Y_time_of_day_15_min_window_29_40%    0.434272
216                       Z_time_of_day_15_min_window_95_90%    0.427277
367                    light_time_of_day_15_min_window_88_3%    0.424115
115                       X_time_of_day_15_min_window_68_10%    0.420524
48                          Y_time_of_day_hour_window_20_sum    0.391182
363                   light_time_of_day_15_min_window_76_std    0.390060
167                       Y_time_of_day_15_min_window_90_20%    0.383440
93     battery_use_since_wear_time_of_day_hour_window_22_50%    0.356776
74                      anglez_time_of_day_hour_window_0_45%    0.347354
312                  anglez_time_of_day_15_min_window_49_95%    0.337596
236                    enmo_time_of_day_15_min_window_40_65%    0.333236
294                  anglez_time_of_day_15_min_window_13_85%    0.332228
92     battery_use_since_wear_time_of_day_hour_window_22_10%    0.331744
244                    enmo_time_of_day_15_min_window_50_75%    0.328085
111                        X_time_of_day_15_min_window_67_5%    0.327029
78                     anglez_time_of_day_hour_window_12_max    0.312762
210                       Z_time_of_day_15_min_window_87_70%    0.304906
266                    enmo_time_of_day_15_min_window_64_65%    0.297335
283                    enmo_time_of_day_15_min_window_90_45%    0.294654
209                        Z_time_of_day_15_min_window_86_3%    0.293090
220                     enmo_time_of_d

In [256]:
unimportant_features_df = catboost_importance_df[catboost_importance_df['Importance'] == 0]
unimportant_features = unimportant_features_df['Feature'].tolist()
print(len(unimportant_features))
unimportant_features[:5]

113


['light_time_of_day_15_min_window_54_5%',
 'X_time_of_day_15_min_window_27_25%',
 'anglez_time_of_day_hour_window_13_3%',
 'X_time_of_day_15_min_window_46_99%',
 'X_time_of_day_15_min_window_1_20%']

In [257]:
selected_train_df = selected_train_df.drop(unimportant_features, axis=1)
print(selected_train_df.shape)
selected_train_df.head()

(996, 284)


id  Basic_Demos-Age  Physical-Height  Physical-Weight  BIA-BIA_FFM  \
0  00115b9f              9.0             56.0             81.6     62.77570   
1  001f3379             13.0             59.5            112.2     84.02850   
2  00f332d1             14.0             66.5            108.0     92.89800   
3  01085eb3             12.0             60.5            178.0    107.48600   
4  012cadd8              9.0             53.2             68.8     62.48774   

   BIA-BIA_FFMI  BIA-BIA_ICW  BIA-BIA_LDM  SDS-SDS_Total_Raw  SDS-SDS_Total_T  \
0       14.0740     30.40410     16.77900               31.0             45.0   
1       16.6877     32.91410     20.90200               40.0             56.0   
2       14.7695     41.40040     24.21580               30.0             43.0   
3       20.6463     47.22380     26.78340               53.0             73.0   
4       14.5418     29.57456     16.84324               27.0             40.0   

   PreInt_EduHx-computerinternet_hoursday  X_weekday_3_min  X_weekday_4_35%  \
0                                     0.0        -0.973490        -0.451854   
1                                     0.0        -1.015088         0.044092   
2                                     2.0        -1.553576         0.110742   
3                                     0.0        -2.284304        -0.683567   
4                                     0.0        -0.988268         0.012306   

   X_weekday_7_75%  X_weekday_7_90%  Y_weekday_2_75%  Z_weekday_2_3%  \
0         0.090599         0.638867         0.652526       -0.965397   
1         0.552708         0.734725         0.193994       -1.010596   
2         0.717873         0.909538         0.414495       -0.873446   
3        -0.004704         0.533553         0.220756       -0.969265   
4         0.829352         0.948852         0.256043       -0.973023   

   Z_weekday_5_std  enmo_weekday_4_20%  light_weekday_1_10%  \
0         0.581047            0.006422             1.941022   
1         0.636366            0.000623             0.744055   
2         0.444914            0.000078             1.312926   
3         0.533165            0.000471             1.364101   
4         0.553874            0.005021             1.995188   

   light_weekday_3_25%  light_weekday_6_70%  \
0             3.691755             7.500000   
1             1.121339             9.282051   
2             1.663496            95.829414   
3             2.543231             6.329125   
4             5.000000             7.855823   

   battery_use_since_wear_weekday_5_3%  X_time_of_day_hour_window_0_55%  \
0                            24.000000                        -0.140323   
1                           120.583252                         0.239299   
2                           127.000000                         0.184166   
3                           102.000000                        -0.173248   
4                            75.000000                        -0.090508   

   X_time_of_day_hour_window_4_80%  X_time_of_day_hour_window_16_50%  \
0                         0.415568                         -0.387578   
1                         0.706599                         -0.043422   
2                         0.818615                          0.314592   
3                         0.368135                         -0.526144   
4                         0.538887                          0.281857   

   X_time_of_day_hour_window_18_20%  X_time_of_day_hour_window_18_50%  \
0                         -0.832833                         -0.531406   
1                         -0.297340                          0.194321   
2                         -0.107338                          0.241027   
3                         -0.882827                         -0.628814   
4                          0.021343                          0.616676   

   X_time_of_day_hour_window_18_70%  X_time_of_day_hour_window_23_min  \
0                         -0.293680                         -0.829557   
1       

In [258]:
CatBoost_Params = {
    'learning_rate': 0.003,
    'depth': 8,
    'iterations': 200,
    'random_seed': SEED,
    'verbose': 1,
    'l2_leaf_reg': 10,  # Increase this value
    'task_type': 'GPU'
}

CatBoost_Model = CatBoostRegressor(
    **CatBoost_Params,
    use_best_model=True
    #custom_metric=[quadratic_weighted_kappa]#,  # Use custom QWK as an additional metric
    #eval_metric=qwk_wrapper       # Optionally use it as the primary evaluation metric
)

catboost_models_list = TrainML(CatBoost_Model, selected_train_df)#, test_final)

0:	learn: 0.7606806	test: 0.7638249	best: 0.7638249 (0)	total: 8.71ms	remaining: 1.73s
1:	learn: 0.7602552	test: 0.7636367	best: 0.7636367 (1)	total: 16.4ms	remaining: 1.63s
2:	learn: 0.7598382	test: 0.7634485	best: 0.7634485 (2)	total: 24ms	remaining: 1.58s
3:	learn: 0.7594210	test: 0.7632931	best: 0.7632931 (3)	total: 31.6ms	remaining: 1.55s
4:	learn: 0.7589647	test: 0.7629984	best: 0.7629984 (4)	total: 39ms	remaining: 1.52s
5:	learn: 0.7586124	test: 0.7627903	best: 0.7627903 (5)	total: 47ms	remaining: 1.52s
6:	learn: 0.7582337	test: 0.7626064	best: 0.7626064 (6)	total: 54.4ms	remaining: 1.5s
7:	learn: 0.7578406	test: 0.7624360	best: 0.7624360 (7)	total: 61.9ms	remaining: 1.49s
8:	learn: 0.7574543	test: 0.7622790	best: 0.7622790 (8)	total: 69.7ms	remaining: 1.48s
9:	learn: 0.7570640	test: 0.7620598	best: 0.7620598 (9)	total: 77.1ms	remaining: 1.47s
10:	learn: 0.7567111	test: 0.7618711	best: 0.7618711 (10)	total: 84.5ms	remaining: 1.45s
11:	learn: 0.7562773	test: 0.7616125	best: 0.761

In [259]:
catboost_importance_df = feature_importance(catboost_models_list[0], selected_train_df.drop(['id', 'sii'], axis=1))
print(catboost_importance_df.shape)
catboost_importance_df

(282, 2)


Feature  Importance
278                                       Internet_Hours_Age   14.798613
277                                                  BMI_Age    6.315199
1                                            Physical-Height    3.840605
9                     PreInt_EduHx-computerinternet_hoursday    3.024046
8                                            SDS-SDS_Total_T    2.606697
279                                       BMI_Internet_Hours    2.596438
7                                          SDS-SDS_Total_Raw    2.536596
176                    enmo_time_of_day_15_min_window_58_75%    1.663067
175                    enmo_time_of_day_15_min_window_58_65%    1.646390
174                    enmo_time_of_day_15_min_window_58_60%    1.409199
239                   light_time_of_day_15_min_window_39_max    1.404488
160                    enmo_time_of_day_15_min_window_39_80%    1.197480
194                    enmo_time_of_day_15_min_window_73_75%    1.082684
163                    enmo_time_of_day_15_min_window_40_75%    0.900352
159                    enmo_time_of_day_15_min_window_39_75%    0.822567
67     battery_use_since_wear_time_of_day_hour_window_22_50%    0.815005
55                      anglez_time_of_day_hour_window_0_60%    0.755099
171                    enmo_time_of_day_15_min_window_53_80%    0.748689
25                          X_time_of_day_hour_window_18_20%    0.723937
233                  anglez_time_of_day_15_min_window_95_50%    0.714559
66     battery_use_since_wear_time_of_day_hour_window_22_10%    0.702870
2                                            Physical-Weight    0.696830
195                    enmo_time_of_day_15_min_window_73_80%    0.693350
240                   light_time_of_day_15_min_window_40_std    0.670210
193                    enmo_time_of_day_15_min_window_73_70%    0.667908
32                          Y_time_of_day_hour_window_16_90%    0.658604
247                   light_time_of_day_15_min_window_61_70%    0.646705
270  battery_use_since_wear_time_of_day_15_min_window_86_65%    0.633080
271  battery_use_since_wear_time_of_day_15_min_window_89_50%    0.618780
169                   enmo_time_of_day_15_min_window_53_mean    0.618449
16                                           Z_weekday_5_std    0.615960
158                    enmo_time_of_day_15_min_window_39_70%    0.614286
269   battery_use_since_wear_time_of_day_15_min_window_85_5%    0.605304
78                         X_time_of_day_15_min_window_67_5%    0.553122
275                                      PAQ_C-Season_Winter    0.543804
53                       enmo_time_of_day_hour_window_22_max    0.533227
162                    enmo_time_of_day_15_min_window_40_70%    0.531209
182                    enmo_time_of_day_15_min_window_62_55%    0.511068
107                       Y_time_of_day_15_min_window_57_95%    0.488440
86                        X_time_of_day_15_min_window_73_20%    0.488209
276                                        Basic_Demos-Sex_1    0.483555
213                  anglez_time_of_day_15_min_window_40_35%    0.480225
257                    light_time_of_day_15_min_window_88_1%    0.469150
91                        X_time_of_day_15_min_window_85_15%    0.459726
259   battery_use_since_wear_time_of_day_15_min_window_7_10%    0.454313
31                          Y_time_of_day_hour_window_10_80%    0.452213
148                       Z_time_of_day_15_min_window_95_90%    0.436991
129                       Z_time_of_day_15_min_window_39_85%    0.429592
108                       Y_time_of_day_15_min_window_57_97%    0.427873
20                                       light_weekday_6_70%    0.417592
145                       Z_time_of_day_15_min_window_94_min    0.415974
0                                            Basic_Demos-Age    0.402999
143                        Z_time_of_day_15_min_window_86_3%    0.400259
44                        enmo_time_of_day_hour_window_9_75%    0.386083
260   battery_use_since_wear_time_of_d

In [260]:
unimportant_features_df = catboost_importance_df[catboost_importance_df['Importance'] == 0]
unimportant_features = unimportant_features_df['Feature'].tolist()
print(len(unimportant_features))
unimportant_features[:5]

25


['Y_time_of_day_15_min_window_71_75%',
 'enmo_time_of_day_15_min_window_62_60%',
 'X_time_of_day_15_min_window_81_30%',
 'anglez_time_of_day_15_min_window_10_10%',
 'Y_time_of_day_15_min_window_45_5%']

In [261]:
selected_train_df = selected_train_df.drop(unimportant_features, axis=1)
print(selected_train_df.shape)
selected_train_df.head()

(996, 259)


id  Basic_Demos-Age  Physical-Height  Physical-Weight  BIA-BIA_FFM  \
0  00115b9f              9.0             56.0             81.6     62.77570   
1  001f3379             13.0             59.5            112.2     84.02850   
2  00f332d1             14.0             66.5            108.0     92.89800   
3  01085eb3             12.0             60.5            178.0    107.48600   
4  012cadd8              9.0             53.2             68.8     62.48774   

   BIA-BIA_ICW  BIA-BIA_LDM  SDS-SDS_Total_Raw  SDS-SDS_Total_T  \
0     30.40410     16.77900               31.0             45.0   
1     32.91410     20.90200               40.0             56.0   
2     41.40040     24.21580               30.0             43.0   
3     47.22380     26.78340               53.0             73.0   
4     29.57456     16.84324               27.0             40.0   

   PreInt_EduHx-computerinternet_hoursday  X_weekday_3_min  X_weekday_4_35%  \
0                                     0.0        -0.973490        -0.451854   
1                                     0.0        -1.015088         0.044092   
2                                     2.0        -1.553576         0.110742   
3                                     0.0        -2.284304        -0.683567   
4                                     0.0        -0.988268         0.012306   

   X_weekday_7_75%  X_weekday_7_90%  Y_weekday_2_75%  Z_weekday_2_3%  \
0         0.090599         0.638867         0.652526       -0.965397   
1         0.552708         0.734725         0.193994       -1.010596   
2         0.717873         0.909538         0.414495       -0.873446   
3        -0.004704         0.533553         0.220756       -0.969265   
4         0.829352         0.948852         0.256043       -0.973023   

   Z_weekday_5_std  enmo_weekday_4_20%  light_weekday_1_10%  \
0         0.581047            0.006422             1.941022   
1         0.636366            0.000623             0.744055   
2         0.444914            0.000078             1.312926   
3         0.533165            0.000471             1.364101   
4         0.553874            0.005021             1.995188   

   light_weekday_3_25%  light_weekday_6_70%  \
0             3.691755             7.500000   
1             1.121339             9.282051   
2             1.663496            95.829414   
3             2.543231             6.329125   
4             5.000000             7.855823   

   battery_use_since_wear_weekday_5_3%  X_time_of_day_hour_window_0_55%  \
0                            24.000000                        -0.140323   
1                           120.583252                         0.239299   
2                           127.000000                         0.184166   
3                           102.000000                        -0.173248   
4                            75.000000                        -0.090508   

   X_time_of_day_hour_window_4_80%  X_time_of_day_hour_window_16_50%  \
0                         0.415568                         -0.387578   
1                         0.706599                         -0.043422   
2                         0.818615                          0.314592   
3                         0.368135                         -0.526144   
4                         0.538887                          0.281857   

   X_time_of_day_hour_window_18_20%  X_time_of_day_hour_window_18_50%  \
0                         -0.832833                         -0.531406   
1                         -0.297340                          0.194321   
2                         -0.107338                          0.241027   
3                         -0.882827                         -0.628814   
4                          0.021343                          0.616676   

   X_time_of_day_hour_window_18_70%  X_time_of_day_hour_window_23_min  \
0                         -0.293680                         -0.829557   
1                          0.552764                         -1.004113   
2                  

In [262]:
CatBoost_Params = {
    'learning_rate': 0.001,
    'depth': 10,
    'iterations': 1000,
    'random_seed': SEED,
    'verbose': 1,
    'l2_leaf_reg': 10,  # Increase this value
    'task_type': 'GPU'
}

CatBoost_Model = CatBoostRegressor(
    **CatBoost_Params,
    use_best_model=True
    #custom_metric=[quadratic_weighted_kappa]#,  # Use custom QWK as an additional metric
    #eval_metric=qwk_wrapper       # Optionally use it as the primary evaluation metric
)

catboost_models_list = TrainML(CatBoost_Model, selected_train_df)#, test_final)

0:	learn: 0.7608911	test: 0.7638765	best: 0.7638765 (0)	total: 82.6ms	remaining: 1m 22s
1:	learn: 0.7607086	test: 0.7637691	best: 0.7637691 (1)	total: 163ms	remaining: 1m 21s
2:	learn: 0.7605271	test: 0.7636417	best: 0.7636417 (2)	total: 243ms	remaining: 1m 20s
3:	learn: 0.7603428	test: 0.7635252	best: 0.7635252 (3)	total: 330ms	remaining: 1m 22s
4:	learn: 0.7601654	test: 0.7634150	best: 0.7634150 (4)	total: 411ms	remaining: 1m 21s
5:	learn: 0.7599839	test: 0.7633034	best: 0.7633034 (5)	total: 492ms	remaining: 1m 21s
6:	learn: 0.7598080	test: 0.7632192	best: 0.7632192 (6)	total: 578ms	remaining: 1m 22s
7:	learn: 0.7596283	test: 0.7631222	best: 0.7631222 (7)	total: 660ms	remaining: 1m 21s
8:	learn: 0.7594384	test: 0.7630027	best: 0.7630027 (8)	total: 740ms	remaining: 1m 21s
9:	learn: 0.7592589	test: 0.7628748	best: 0.7628748 (9)	total: 827ms	remaining: 1m 21s
10:	learn: 0.7591081	test: 0.7627477	best: 0.7627477 (10)	total: 908ms	remaining: 1m 21s
11:	learn: 0.7589318	test: 0.7626234	bes

In [ ]:
train_one_hot = train_nonan.copy()
test_one_hot = test_merge.copy()

In [ ]:
for col in cat_cols:
    if 'PCIAT' not in col:
        train_sr = train_one_hot[col].fillna('Missing').apply(str)        
        test_sr = test_one_hot[col].fillna('Missing').apply(str)
        train_one_hot[col] = train_sr
        test_one_hot[col] = test_sr
        concat_sr = pd.concat([train_sr, test_sr])
        unique_list = sorted(concat_sr.unique().tolist())

        for v in unique_list:
            new_col_name = col + '_' + v
            train_one_hot[new_col_name] = pd.Series(train_one_hot[col] == v).astype(int)
            test_one_hot[new_col_name] = pd.Series(test_one_hot[col] == v).astype(int)
    else:
        train_sr = train_one_hot[col].fillna('Missing').apply(str)
        train_one_hot[col] = train_sr
        unique_list = sorted(train_sr.unique().tolist())

        for v in unique_list:
            new_col_name = col + '_' + v
            train_one_hot[new_col_name] = pd.Series(train_one_hot[col] == v).astype(int)

train_one_hot.drop(cat_cols, axis=1, inplace=True)
test_one_hot.drop([col for col in cat_cols if 'PCIAT' not in col], axis=1, inplace=True)

In [ ]:
print(train_ts.shape)
train_ts.head()

In [ ]:
print(train_one_hot.shape)
train_one_hot.head()

In [ ]:
print(test_one_hot.shape)
test_one_hot.head()

In [ ]:
train_one_hot.drop('id', axis=1, inplace=True)
test_one_hot.drop('id', axis=1, inplace=True)

In [ ]:
train = train_one_hot[test_one_hot.columns.tolist() + ['sii']].copy()
test = test_one_hot.copy()

In [ ]:
print(train.shape)
train.head()

In [ ]:
print(test.shape)
test.head()

In [ ]:
concat_df = pd.concat([train[test.columns], test], ignore_index=True)
print(concat_df.shape)
concat_df.head()

In [ ]:
imputer = KNNImputer(n_neighbors=5)
imputed_data_concat = imputer.fit_transform(concat_df)

In [ ]:
concat_imputed = pd.DataFrame(imputed_data_concat, columns=concat_df.columns)
print(concat_imputed.shape)
concat_imputed.head()

In [ ]:
concat_imputed.isna().sum().sum()

In [ ]:
concat_imputed = feature_engineering(concat_imputed)
print(concat_imputed.shape)
concat_imputed.head()

In [ ]:
if np.any(np.isinf(concat_imputed)):
    print('inf in data')
    concat_imputed = concat_imputed.replace([np.inf, -np.inf], np.nan)

In [ ]:
imputer = KNNImputer(n_neighbors=5)
imputed_data = imputer.fit_transform(concat_imputed)

In [ ]:
concat_imputed = pd.DataFrame(imputed_data, columns=concat_imputed.columns)
print(concat_imputed.shape)
concat_imputed.head()

In [ ]:
concat_imputed.isna().sum().sum()

In [ ]:
train_imputed = concat_imputed.head(train.shape[0]).reset_index(drop=True)
test_imputed = concat_imputed.tail(test.shape[0]).reset_index(drop=True)

In [ ]:
train_imputed['sii'] = train['sii']

In [ ]:
train_final = train_imputed.copy()
test_final = test_imputed.copy()

In [ ]:
print(train_final.shape)
print(test_final.shape)

# Model Training and Evaluation

- **Model Types**: Various models are used, including:
  - **LightGBM**: A gradient-boosting framework known for its speed and efficiency with large datasets.
  - **XGBoost**: Another powerful gradient-boosting model used for structured data.
  - **CatBoost**: Optimized for categorical features without the need for extensive preprocessing.
  - **Voting Regressor**: An ensemble model that combines the predictions of LightGBM, XGBoost, and CatBoost for better accuracy.
- **Cross-Validation**: Stratified K-Folds cross-validation is employed to split the data into training and validation sets, ensuring balanced class distribution in each fold.
- **Quadratic Weighted Kappa (QWK)**: The performance of the models is evaluated using QWK, which measures the agreement between predicted and actual values, taking into account the ordinal nature of the target variable.
- **Threshold Optimization**: The `minimize` function from `scipy.optimize` is used to fine-tune decision thresholds that map continuous predictions to discrete categories (None, Mild, Moderate, Severe).


In [ ]:
def TrainML(model_class, train_data, test_data):
    X = train_data.drop(['sii'], axis=1)
    y = train_data['sii']

    SKF = StratifiedKFold(n_splits=n_splits, shuffle=True, random_state=SEED)
    
    train_S = []
    test_S = []
    
    oof_non_rounded = np.zeros(len(y), dtype=float) 
    oof_rounded = np.zeros(len(y), dtype=int) 
    test_preds = np.zeros((len(test_data), n_splits))

    for fold, (train_idx, test_idx) in enumerate(tqdm(SKF.split(X, y), desc="Training Folds", total=n_splits)):
        X_train, X_val = X.iloc[train_idx], X.iloc[test_idx]
        y_train, y_val = y.iloc[train_idx], y.iloc[test_idx]

        model = clone(model_class)
        model.fit(X_train, y_train)

        y_train_pred = model.predict(X_train)
        y_val_pred = model.predict(X_val)

        oof_non_rounded[test_idx] = y_val_pred
        y_val_pred_rounded = y_val_pred.round(0).astype(int)
        oof_rounded[test_idx] = y_val_pred_rounded

        train_kappa = quadratic_weighted_kappa(y_train, y_train_pred.round(0).astype(int))
        val_kappa = quadratic_weighted_kappa(y_val, y_val_pred_rounded)

        train_S.append(train_kappa)
        test_S.append(val_kappa)
        
        test_preds[:, fold] = model.predict(test_data)
        
        print(f"Fold {fold+1} - Train QWK: {train_kappa:.4f}, Validation QWK: {val_kappa:.4f}")
        clear_output(wait=True)

    print(f"Mean Train QWK --> {np.mean(train_S):.4f}")
    print(f"Mean Validation QWK ---> {np.mean(test_S):.4f}")

    KappaOPtimizer = minimize(evaluate_predictions,
                              x0=[0.5, 1.5, 2.5], args=(y, oof_non_rounded), 
                              method='Nelder-Mead')
    assert KappaOPtimizer.success, "Optimization did not converge."
    
    oof_tuned = threshold_Rounder(oof_non_rounded, KappaOPtimizer.x)
    tKappa = quadratic_weighted_kappa(y, oof_tuned)

    print(f"----> || Optimized QWK SCORE :: {Fore.CYAN}{Style.BRIGHT} {tKappa:.3f}{Style.RESET_ALL}")

    tpm = test_preds.mean(axis=1)
    tpTuned = threshold_Rounder(tpm, KappaOPtimizer.x)
    
    submission = pd.DataFrame({
        'id': sample['id'],
        'sii': tpTuned
    })

    return submission


# Hyperparameter Tuning

- **LightGBM Parameters**: Hyperparameters such as `learning_rate`, `max_depth`, `num_leaves`, and `feature_fraction` are tuned to improve the performance of the LightGBM model. These parameters control the complexity of the model and its ability to generalize to new data.
- **XGBoost and CatBoost Parameters**: Similar tuning is applied for XGBoost and CatBoost, adjusting parameters such as `n_estimators`, `max_depth`, `learning_rate`, `subsample`, and `regularization` terms (`reg_alpha`, `reg_lambda`). These help in controlling overfitting and ensuring the model's robustness.

In [ ]:
Params7 = {
    'learning_rate': 0.03884249148676395,
    'max_depth': 12,
    'num_leaves': 413,
    'min_data_in_leaf': 14,
    'feature_fraction': 0.7987976913702801,
    'bagging_fraction': 0.7602261703576205,
    'bagging_freq': 2,
    'lambda_l1': 4.735462555910575,
    'lambda_l2': 4.735028557007343e-06
} # CV : 0.4094 | LB : 0.471

In [ ]:
Light = LGBMRegressor(**Params7, random_state=SEED, verbose=-1, n_estimators=200)

In [ ]:
Submission1 = TrainML(Light, train_final, test_final)
Submission1.to_csv('submission.csv', index=False)

Submission1